# **Importing Required Packages and Libraries**

In [54]:
!pip install yfinance # For downloading historical stock price data

In [55]:
!pip install YahooQuery # For fetching financial statements and key metrics

In [56]:
!pip install arch # ARCH and GARCH models for volatility analysis

In [57]:
!pip install statsmodels # For econometric models and statistical tests

In [58]:
!pip install ta # Technical analysis indicators (moving averages, RSI, etc.)

In [59]:
!pip install plotly # Interactive visualization

In [60]:
!pip install finta # Financial indicators

In [61]:
# ========================== CORE LIBRARIES ==========================
import numpy as np                        # Numerical operations
import numpy.random as rn                 # Random number generation
import pandas as pd                       # DataFrame handling
import datetime as dt                     # Date and time manipulation
import warnings                           # Warning management
warnings.filterwarnings("ignore")         # Suppress warnings

# =================== FINANCIAL DATA ACQUISITION ====================
import yfinance as yf                     # Historical market data
from yahooquery import Ticker             # Extended financial and fundamental data

# ===================== TECHNICAL INDICATORS ========================
import ta                                 # General technical indicators
from ta.volatility import BollingerBands
from ta.trend import ADXIndicator, IchimokuIndicator
from ta.momentum import StochasticOscillator
from finta import TA                      # Alternative indicators (e.g., VWAP, EMA)

# ================ TECHNICAL PATTERN TOOLS ==========================
from scipy.signal import argrelextrema    # Local extrema detection (peaks/troughs)

# ===================== TIME SERIES ANALYSIS ========================
from statsmodels.tsa.arima.model import ARIMA             # ARIMA modeling
from statsmodels.tsa.api import VAR                       # Vector Autoregression
from statsmodels.regression.linear_model import OLS       # OLS Regression
from statsmodels.tsa.seasonal import seasonal_decompose   # Trend-seasonality decomposition
from statsmodels.tsa.stattools import acf                 # Autocorrelation function
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from statsmodels.graphics.gofplots import qqplot
import statsmodels.api as sm                              # General API

# =================== VOLATILITY & RESIDUAL DIAGNOSTICS =============
from arch import arch_model                               # GARCH/ARCH models
from statsmodels.stats.stattools import jarque_bera       # Normality test
from statsmodels.stats.diagnostic import het_arch, acorr_ljungbox  # ARCH & Ljung-Box tests

# ===================== DISTRIBUTIONAL ANALYSIS =====================
from scipy import stats                                    # General statistics
from scipy.stats import (
    skew, kurtosis, probplot,
    norm, t as student_t, chi2                             # Key distributions
)

# ===================== MACHINE LEARNING TOOLS ======================
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import (
    classification_report, confusion_matrix,
    mean_absolute_error, mean_squared_error
)

# ================== MODEL SELECTION & UTILITIES ====================
import itertools                                           # Grid search, permutations
from typing import Union, Tuple, List                     # Type hinting

# ===================== VISUALIZATION TOOLS =========================
import matplotlib.pyplot as plt
import matplotlib.dates as mdates                         # Date formatting for plots
import seaborn as sns
sns.set(style="whitegrid")

import plotly.graph_objects as go                         # Advanced visuals
import plotly.express as px                               # Quick interactive plots
from plotly.subplots import make_subplots                 # Multi-plot layout

# ====================== NOTEBOOK UTILITIES =========================
from tqdm.notebook import tqdm                            # Progress bars
import ipywidgets as widgets                              # Interactive widgets
from IPython.display import display, HTML, clear_output, Markdown
import textwrap                                           # Text formatting


# **Exploratory Data Analysis (EDA)**

## **Company Overview: NVIDIA Corporation (`NVDA`)**

Before performing exploratory data analysis or building predictive models, it's essential to understand the company's **fundamental profile** and **financial context**. This section compiles comprehensive data from Yahoo Finance including:

- Basic risk metrics (e.g., **CAPM Beta**)
- Shareholding structure
- Historical **dividends** and **stock splits**
- Detailed **financial statements**
- Latest **news articles**

---

### **Data Modules Included:**

| Module                   | Description                                                  |
|--------------------------|--------------------------------------------------------------|
| **Basic Info**         | Includes CAPM Beta and core metadata                         |
| **Holders**            | Major, institutional, and mutual fund holders                |
| **Dividends & Splits** | Historical dividend payouts and stock split history          |
| **Financials**         | Income statements, balance sheets, and cash flow reports     |
| **News**               | Recent headlines from financial publishers                   |

---

### **Interactive Tabbed View:**
The data is displayed in a **clickable tab layout** to allow smooth navigation without cluttering the notebook. Each tab contains a well-formatted table with relevant financial insights.

> This section acts as a *"fundamental dashboard"* — empowering informed modeling and interpretation in the rest of the analysis.

> **Note:** Data is retrieved live via `yfinance`, and all retrieval processes are wrapped in error handling for robustness.

---

In [62]:
# Configuration
TICKER_SYMBOL_INFO = 'NVDA'
print(f"🔍 Fetching data for: {TICKER_SYMBOL_INFO}")

# Create Ticker Object
ticker_info = yf.Ticker(TICKER_SYMBOL_INFO)

# Section 1: Basic Company Info
try:
    info = ticker_info.info
    capm_beta = info.get('beta', 'N/A')
    sector = info.get('sector', 'N/A')
    industry = info.get('industry', 'N/A')
    print(f"✅ Basic Info Retrieved:")
    print(f"   • Sector: {sector}")
    print(f"   • Industry: {industry}")
    print(f"   • CAPM Beta: {capm_beta}")
except Exception as e:
    print(f"❌ Error fetching basic info: {e}")
    info = {}
    capm_beta = 'Unavailable'

# Section 2: Shareholders
try:
    major_holders = ticker_info.major_holders
    institutional_holders = ticker_info.institutional_holders
    mutual_fund_holders = ticker_info.mutualfund_holders
except Exception as e:
    print(f"❌ Error fetching holder info: {e}")
    major_holders = institutional_holders = mutual_fund_holders = pd.DataFrame()

# Section 3: Dividends and Splits
try:
    actions = ticker_info.actions
    dividends = ticker_info.dividends
    splits = ticker_info.splits
except Exception as e:
    print(f"❌ Error fetching dividend/split info: {e}")
    actions = dividends = splits = pd.DataFrame()

# Section 4: Financial Statements
try:
    stat_inc = ticker_info.income_stmt
    stat_inc_q = ticker_info.quarterly_income_stmt
    stat_bal = ticker_info.balance_sheet
    stat_bal_q = ticker_info.quarterly_balance_sheet
    stat_cf = ticker_info.cashflow
    stat_cf_q = ticker_info.quarterly_cashflow
except Exception as e:
    print(f"❌ Error fetching financials: {e}")
    stat_inc = stat_inc_q = stat_bal = stat_bal_q = stat_cf = stat_cf_q = pd.DataFrame()

# Section 5: News Articles
try:
    news = ticker_info.news

    if isinstance(news, list) and all(isinstance(article, dict) for article in news):
        print("\n📰 Top 5 Recent News:")
        for i, article in enumerate(news[:5]):
            title = article.get('title', 'No Title')
            publisher = article.get('publisher', 'Unknown')
            link = article.get('link', 'No Link')
            print(f"{i+1}. {title}")
            print(f"   📌 Publisher: {publisher}")
            print(f"   🔗 Link: {link}\n")
    else:
        print("⚠️ News structure not as expected or empty.")
        news = []
except Exception as e:
    print(f"❌ Error fetching news: {e}")
    news = []


# Display in Tabs
tab_titles = [
    "📊 Major Holders",
    "🏛️ Institutional Holders",
    "🏦 Mutual Fund Holders",
    "💰 Dividends",
    "🔀 Splits",
    "📃 Annual Income",
    "📄 Quarterly Income",
    "📃 Annual Balance",
    "📄 Quarterly Balance",
    "📃 Annual Cash Flow",
    "📄 Quarterly Cash Flow"
]

tab_contents = [
    major_holders,
    institutional_holders,
    mutual_fund_holders,
    dividends,
    splits,
    stat_inc.head(),
    stat_inc_q.head(),
    stat_bal.head(),
    stat_bal_q.head(),
    stat_cf.head(),
    stat_cf_q.head()
]

children = [widgets.Output() for _ in tab_contents]
tabs = widgets.Tab()
tabs.children = children

for i, title in enumerate(tab_titles):
    tabs.set_title(i, title)

for out, content in zip(children, tab_contents):
    with out:
        display(content)

display(tabs)

print("✅ All sections loaded.")


🔍 Fetching data for: NVDA
✅ Basic Info Retrieved:
   • Sector: Technology
   • Industry: Semiconductors
   • CAPM Beta: 2.122

📰 Top 5 Recent News:
1. No Title
   📌 Publisher: Unknown
   🔗 Link: No Link

2. No Title
   📌 Publisher: Unknown
   🔗 Link: No Link

3. No Title
   📌 Publisher: Unknown
   🔗 Link: No Link

4. No Title
   📌 Publisher: Unknown
   🔗 Link: No Link

5. No Title
   📌 Publisher: Unknown
   🔗 Link: No Link



✅ All sections loaded.


## **Configuration Summary: Time Series & Portfolio Scope**
This analysis is based on historical **adjusted close prices**, **simple returns**, and **logarithmic returns** for selected technology stocks over a multi-year period.

- **Stocks Analyzed:** NVDA, MSFT, INTC, AMD, ADBE  
- **Time Range:** January 1, 2020 – June 5, 2025  
- **Data Frequency:** Daily (`1d`)  
- **Data Source:** Yahoo Finance via `yfinance` API

---

## **Purpose and Content**

This notebook section provides an interactive, tab-based summary for each dataset, consisting of three parts:

### **Adjusted Close Prices**
- Adjusted for dividends and stock splits.
- Reflects true long-term asset performance.
- Includes structural information and missing value checks.

### **Simple Returns**
- Formula: $R_t = \frac{P_t}{P_{t-1}} - 1$
- Indicates the daily percentage change in stock prices.
- Useful for calculating volatility, beta, and correlations.

### **Logarithmic Returns**
- Formula: $r_t = \ln\left(\frac{P_t}{P_{t-1}}\right)$
- Preferred in quantitative finance due to properties like time additivity.
- Closer to normal distribution, ideal for modeling.

---

## **Tab Description**

Each tab contains the following sections:

| Section | Description |
|--------|-------------|
| Structure | Column names, non-null counts, and data types |
| Descriptive Statistics | Summary metrics such as mean, std, min–max |
| Sample Rows | First and last 5 records for quick inspection |

---

### **Notes**

- If no data is available for a tab, a warning message is shown instead.
- This EDA tool is designed to be fully compatible with `ipywidgets`, `pandas`, `numpy`, and `yfinance`.

---

In [63]:
# Configuration
TICKERS = ["NVDA", "MSFT", "INTC", "AMD", "ADBE"]
START_DATE = "2020-01-01"
END_DATE = "2025-06-06"
INTERVAL = "1d"

# Download Historical Adjusted Close Data
try:
    print(f"\n📥 Downloading adjusted close data for: {', '.join(TICKERS)}")
    data = yf.download(
        tickers=TICKERS,
        start=START_DATE,
        end=END_DATE,
        interval=INTERVAL,
        group_by="column",
        auto_adjust=False
    )

    prices = data['Adj Close'].dropna(how='all')  # Clean missing
    print("✅ Data download complete.")
except Exception as e:
    print(f"❌ Error during data download: {e}")
    prices = pd.DataFrame()

# Calculate Returns
try:
    pct_returns = prices.pct_change().dropna(how='all')
    log_returns = np.log(prices / prices.shift(1)).dropna(how='all')
except Exception as e:
    print(f"❌ Error during return calculation: {e}")
    pct_returns = pd.DataFrame()
    log_returns = pd.DataFrame()

# Create EDA Summary Panels
def structure_table(df):
    return pd.DataFrame({
        'Column': df.columns,
        'Non-Null Count': df.notnull().sum().values,
        'Dtype': df.dtypes.values
    })

def stats_table(df):
    return df.describe()

def samples_table(df):
    return pd.concat([df.head(), df.tail()])

# Prepare tab content for each dataset
tabs_data = {
    "📘 Adjusted Close Prices": prices,
    "📈 Simple Returns": pct_returns,
    "📉 Log Returns": log_returns
}

# Create Tabs
tab_contents = []
tab_titles = []

for label, df in tabs_data.items():
    if df.empty:
        output = widgets.Output()
        with output:
            display(Markdown(f"### ⚠️ {label} - No data available."))
    else:
        output = widgets.Output()
        with output:
            display(Markdown(f"## 🔎 {label} - Structure"))
            display(structure_table(df))
            display(Markdown(f"## 📊 {label} - Descriptive Stats"))
            display(stats_table(df))
            display(Markdown(f"## 🧾 {label} - First & Last Rows"))
            display(samples_table(df))

    tab_contents.append(output)
    tab_titles.append(label)

# Combine into interactive tabs
tabs = widgets.Tab(children=tab_contents)
for i, title in enumerate(tab_titles):
    tabs.set_title(i, title)

display(Markdown("## 📂 EDA Summary Report with Tabs"))
display(tabs)


[*********************100%***********************]  5 of 5 completed


📥 Downloading adjusted close data for: NVDA, MSFT, INTC, AMD, ADBE
✅ Data download complete.


## 📂 EDA Summary Report with Tabs

## **Stock Price and Return Visualization: NVDA**

This section provides an interactive visualization of **NVIDIA Corporation (NVDA)** based on historical financial data between January 2020 and June 2025.

---

## **Objective**

To present a dual-panel time series analysis of:
1. **Adjusted Close Price** – to track long-term value and price trends.
2. **Daily Simple Returns** – to monitor short-term volatility and return behavior.

---

## **Visualization Details**

### **Upper Panel – Adjusted Close Price**
- Displays the price of NVDA stock over time.
- Adjusted for corporate actions such as splits and dividends.
- Interactive hover tool shows:
  - **Date**
  - **Price (in USD)**

### **Lower Panel – Daily Simple Returns**
- Shows the daily percentage change in NVDA stock price:
  $
  R_t = \frac{P_t - P_{t-1}}{P_{t-1}}
  $
- Useful for detecting volatility, risk, and sharp market moves.
- Rendered using a **dotted crimson line** for contrast and clarity.

---

## 🎨 Styling & Layout Enhancements
- **Responsive size:** 1100x650 pixels.
- **Plotly template:** `plotly_white` for professional readability.
- **Unified hover mode:** Makes cross-panel inspection easier.
- **Axis formatting:**
  - X-axis shows monthly ticks (`%b %Y`)
  - Y-axis includes clear unit labels for price and return

---

In [64]:
ticker = 'NVDA'

# Fallback for start index if out of bounds
if 'prices' in globals() and ticker in prices.columns:
    start_index = min(1001, len(prices[ticker]) - 1)
    dates = prices.index[start_index:]
else:
    raise ValueError(f"'{ticker}' not found in 'prices'. Please check the dataset.")

# Plot
fig = make_subplots(
    rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.08,
    subplot_titles=(f"📈 {ticker} Stock Price", f"📉 {ticker} Daily Simple Returns", f"📈 {ticker} Log Returns") # Added title for the third subplot
)

# Subplot 1: Adjusted Close Price
fig.add_trace(
    go.Scatter(
        x=dates,
        y=prices[ticker].iloc[start_index:],
        mode='lines',
        name=f'{ticker} Price',
        line=dict(color='navy', width=2),
        hovertemplate='Date: %{x|%Y-%m-%d}<br>Price: $%{y:.2f}'
    ),
    row=1, col=1
)

# Subplot 2: Daily Returns
fig.add_trace(
    go.Scatter(
        x=dates,
        y=pct_returns[ticker].iloc[start_index:],
        mode='lines',
        name=f'{ticker} Daily Return',
        line=dict(color='crimson', width=1.5, dash='dot'),
        hovertemplate='Date: %{x|%Y-%m-%d}<br>Return: %{y:.3%}'
    ),
    row=2, col=1
)

# Subplot 3: Log Returns
fig.add_trace(
    go.Scatter(
        x=dates,
        y=log_returns[ticker].iloc[start_index:],
        mode='lines',
        name=f'{ticker} Log Return',
        line=dict(color='crimson', width=1.5, dash='dot'),
        hovertemplate='Date: %{x|%Y-%m-%d}<br>Return: %{y:.3%}'
    ),
    row=3, col=1
)

# Layout Enhancements
fig.update_layout(
    height=650,
    width=1100,
    title={
        'text': f"{ticker} – Price & Return Time Series Analysis",
        'x': 0.5,
        'xanchor': 'center',
        'font': dict(size=22)
    },
    template='plotly_white',
    hovermode='x unified',
    margin=dict(l=60, r=60, t=80, b=60),
    showlegend=False
)

# Axis Titles
fig.update_yaxes(title_text='Adjusted Price ($)', row=1, col=1)
fig.update_yaxes(title_text='Daily Return (%)', row=2, col=1)
fig.update_yaxes(title_text='Log Return (%)', row=3, col=1)
fig.update_xaxes(title_text='Date', tickformat='%b\n%Y', row=3, col=1)

# Show plot
fig.show()


## **Adjusted Closing Prices of Selected Tech Stocks**

This interactive line chart visualizes the **adjusted closing prices** of the following major technology stocks over the selected date range:

- 🟦 NVIDIA (NVDA)  
- 🟪 Microsoft (MSFT)  
- 🟥 Intel (INTC)  
- 🟨 AMD  
- 🟫 Adobe (ADBE)

---

### **Purpose**

The goal of this chart is to allow visual comparison of price trends across multiple tickers. It facilitates:

- Identifying relative performance among selected companies  
- Spotting major price movements and market trends  
- Gaining insight for **portfolio diversification** or **momentum trading strategies**

---

### **Chart Features**

- **X-axis:** Date range (daily granularity)  
- **Y-axis:** Adjusted closing price in USD  
- **Color-coded lines:** One for each ticker for clarity  
- **Interactive hover:** Unified hover mode shows prices of all stocks on the same date  
- **Legend:** Located at the top-right to distinguish tickers

---

### **Styling Enhancements**

- Clean and minimalistic `plotly_white` theme  
- Unified hover mode for comparative insights  
- Professional typography and spacing for presentation and reporting purposes

---

### **Notes**

- Prices are **adjusted** for splits and dividends to reflect total return more accurately.  
- This chart is useful for both **exploratory data analysis (EDA)** and for communicating trends in presentations or dashboards.

---

In [65]:
# Interactive Price Movement Plot

# Create a professional line chart for adjusted close prices
fig = px.line(
    prices,
    x=prices.index,
    y=TICKERS,
    title=f"📊 Adjusted Closing Prices of {', '.join(TICKERS)}",
    labels={
        "value": "Adjusted Close Price (USD)",
        "variable": "Stock Ticker",
        "index": "Date"
    }
)

# Update layout for clarity and aesthetics
fig.update_layout(
    template="plotly_white",
    title_font_size=20,
    xaxis_title="Date",
    yaxis_title="Price (USD)",
    hovermode="x unified",
    legend_title="Ticker",
    margin=dict(l=0, r=0, t=60, b=0)
)

# Display the figure
fig.show()


\# **Option Expiration Dates – NVIDIA (NVDA)**

This module retrieves the **option expiration dates** for the selected stock ticker – `NVDA` (NVIDIA Corporation).

---

## **Downloading NASDAQ-Listed Symbols (Live from FTP)**

To dynamically reference current NASDAQ-listed companies, we fetch the latest ticker list from the **NASDAQ Trader FTP** directory. This ensures that our analysis pipeline is aligned with the most recent exchange listings.

### **Source:**
- FTP URL: `ftp://ftp.nasdaqtrader.com/SymbolDirectory/nasdaqlisted.txt`
- Format: Pipe (`|`) separated text file

### **Workflow Steps:**
1. **Download & Parse**:
   - The file is loaded using `pandas.read_csv()` with the correct delimiter.
2. **Clean Metadata**:
   - The last row (containing file creation timestamp) is removed.
3. **Extract Symbols**:
   - The column `"Symbol"` is converted to a list `tlNASDAQ` for use in filtering or screening.

---

In [66]:
# Configuration
nasdaq_url = "ftp://ftp.nasdaqtrader.com/SymbolDirectory/nasdaqlisted.txt"

print("🔄 Downloading NASDAQ listed symbols...")

try:
    # Read the file using pandas from FTP with appropriate separator
    nasdaq_df = pd.read_csv(nasdaq_url, sep='|')

    # Drop the footer row which contains metadata (e.g., "File Creation Time:")
    nasdaq_df = nasdaq_df[~nasdaq_df['Symbol'].str.contains("File Creation Time", na=False)]

    # Clean and convert the symbol column to string safely
    nasdaq_df['Symbol'] = nasdaq_df['Symbol'].fillna('').astype(str)

    # Extract the list of symbols
    tlNASDAQ = nasdaq_df['Symbol'].tolist()

    # Summary Output
    print(f"✅ Total NASDAQ-listed companies: {len(tlNASDAQ):,}")
    print(f"🎯 Example Symbols: {tlNASDAQ[:50]}")

except Exception as e:
    print(f"❌ Error fetching NASDAQ symbols: {e}")
    tlNASDAQ = []


🔄 Downloading NASDAQ listed symbols...
✅ Total NASDAQ-listed companies: 4,891
🎯 Example Symbols: ['AACB', 'AACBR', 'AACBU', 'AACG', 'AACIU', 'AADR', 'AAL', 'AAME', 'AAOI', 'AAON', 'AAPB', 'AAPD', 'AAPG', 'AAPL', 'AAPU', 'AARD', 'AAVM', 'AAXJ', 'ABAT', 'ABCL', 'ABCS', 'ABEO', 'ABIG', 'ABL', 'ABLLL', 'ABLLW', 'ABLV', 'ABLVW', 'ABNB', 'ABOS', 'ABP', 'ABPWW', 'ABSI', 'ABTS', 'ABUS', 'ABVC', 'ABVE', 'ABVEW', 'ABVX', 'ACAD', 'ACB', 'ACDC', 'ACET', 'ACGL', 'ACGLN', 'ACGLO', 'ACHC', 'ACHV', 'ACIC', 'ACIU']


In [67]:
# Configuration
TICKER_SYMBOL = 'NVDA'

print(f"🔄 Fetching option expiration dates for {TICKER_SYMBOL}...")

try:
    # Create a ticker object
    ticker = yf.Ticker(TICKER_SYMBOL)

    # Get the expiration dates
    expirations = ticker.options

    # Output Summary
    print(f"📌 Total Expiration Dates for {TICKER_SYMBOL}: {len(expirations)}")
    display(HTML(f"<b>🎯 Expiration Dates (first 10 shown):</b> {expirations[:10]}"))

except Exception as e:
    print(f"❌ Error fetching option data for {TICKER_SYMBOL}: {e}")
    expirations = []


🔄 Fetching option expiration dates for NVDA...
📌 Total Expiration Dates for NVDA: 20


## **Call Option Chain Retrieval – NVIDIA (NVDA)**

This section focuses on retrieving the **Call Option Chain** for `NVDA` using the **6th expiration date** (index `5`) obtained in the previous step.

---

### **Purpose**

The aim is to fetch detailed data about all available **call options** for a specific expiration date. This includes:

- Strike prices
- Last traded price
- Bid and ask prices
- Implied volatility
- Open interest and volume

These details are crucial for:

- Analyzing market expectations and positioning
- Building strategies (e.g., covered calls, long calls, bull call spreads)
- Calculating theoretical values and sensitivities (Greeks)

---

### **Selected Expiration**

- **Index:** `5`
- **Date:** Dynamically selected from the `expirations` list
- **Ticker:** `NVDA`

---

### **Output Summary**

- Total number of **call options** listed for this expiration date is printed
- A full DataFrame of the **call option chain** is displayed
- The data is stored in the variable `c` for future use

---

### **Error Handling**

- If the specified index is out of bounds, a user-friendly error message is shown
- General exceptions are also caught and reported

---

In [68]:
# Select a specific expiration date
try:
    selected_expiration_index = 5
    selected_expiration_date = expirations[selected_expiration_index]
    print(f"✅ Selected Expiration Date (Index {selected_expiration_index}): {selected_expiration_date}")

    # Fetch call option chain
    c = ticker.option_chain(selected_expiration_date).calls

    # Output Summary
    print(f"📌 Number of Call Options for {TICKER_SYMBOL} ({selected_expiration_date}): {len(c)}")

    # Display the DataFrame
    display(HTML(f"<b>🎯 Call Option Chain for {TICKER_SYMBOL} - Expiration: {selected_expiration_date}</b>"))
    display(c)

except IndexError:
    print(f"❌ Error: Expiration index {selected_expiration_index} is out of range. Only {len(expirations)} dates available.")

except Exception as e:
    print(f"❌ Error fetching call options for expiration {selected_expiration_index}: {e}")
    c = pd.DataFrame()


✅ Selected Expiration Date (Index 5): 2025-07-18
📌 Number of Call Options for NVDA (2025-07-18): 50


contractSymbol             lastTradeDate  strike  lastPrice     bid  \
0   NVDA250718C00005000 2025-06-09 17:21:17+00:00     5.0     138.19  137.30   
1   NVDA250718C00010000 2025-06-09 18:49:31+00:00    10.0     133.00  132.65   
2   NVDA250718C00015000 2025-06-06 17:39:37+00:00    15.0     127.19  127.55   
3   NVDA250718C00020000 2025-06-09 19:31:48+00:00    20.0     122.72  122.20   
4   NVDA250718C00025000 2025-06-06 17:39:37+00:00    25.0     117.23  117.45   
5   NVDA250718C00030000 2025-05-27 15:31:24+00:00    30.0     105.40  112.85   
6   NVDA250718C00035000 2025-06-06 17:39:37+00:00    35.0     107.33  107.30   
7   NVDA250718C00040000 2025-06-09 15:06:43+00:00    40.0     104.50  102.70   
8   NVDA250718C00045000 2025-05-21 17:26:40+00:00    45.0      89.18   97.75   
9   NVDA250718C00050000 2025-06-10 14:16:48+00:00    50.0      92.95   92.80   
10  NVDA250718C00055000 2025-06-09 19:56:15+00:00    55.0      87.83   87.55   
11  NVDA250718C00060000 2025-06-10 15:53:12+00:00    60.0      83.10   83.00   
12  NVDA250718C00065000 2025-06-09 18:59:05+00:00    65.0      78.31   77.60   
13  NVDA250718C00070000 2025-06-10 14:01:37+00:00    70.0      72.93   72.95   
14  NVDA250718C00075000 2025-06-10 14:23:48+00:00    75.0      68.35   67.95   
15  NVDA250718C00080000 2025-06-10 14:02:31+00:00    80.0      63.17   63.00   
16  NVDA250718C00085000 2025-06-10 15:33:09+00:00    85.0      57.10   58.15   
17  NVDA250718C00090000 2025-06-10 14:46:56+00:00    90.0      53.20   52.95   
18  NVDA250718C00095000 2025-06-09 17:40:08+00:00    95.0      48.50   48.20   
19  NVDA250718C00100000 2025-06-10 16:16:07+00:00   100.0      43.55   43.35   
20  NVDA250718C00105000 2025-06-10 16:00:26+00:00   105.0      38.85   38.35   
21  NVDA250718C00110000 2025-06-10 16:04:29+00:00   110.0      33.90   33.50   
22  NVDA250718C00115000 2025-06-10 15:43:16+00:00   115.0      28.40   28.65   
23  NVDA250718C00120000 2025-06-10 16:22:22+00:00   120.0      24.35   24.20   
24  NVDA250718C00125000 2025-06-10 16:21:15+00:00   125.0      19.85   19.80   
25  NVDA250718C00130000 2025-06-10 16:06:13+00:00   130.0      15.75   15.50   
26  NVDA250718C00135000 2025-06-10 16:13:41+00:00   135.0      11.85   11.75   
27  NVDA250718C00140000 2025-06-10 16:21:47+00:00   140.0       8.60    8.55   
28  NVDA250718C00145000 2025-06-10 16:22:30+00:00   145.0       5.90    5.90   
29  NVDA250718C00150000 2025-06-10 16:21:16+00:00   150.0       3.91    3.90   
30  NVDA250718C00155000 2025-06-10 16:14:59+00:00   155.0       2.48    2.43   
31  NVDA250718C00160000 2025-06-10 16:22:56+00:00   160.0       1.50    1.49   
32  NVDA250718C00165000 2025-06-10 16:18:57+00:00   165.0       0.92    0.91   
33  NVDA250718C00170000 2025-06-10 16:10:22+00:00   170.0       0.58    0.56   
34  NVDA250718C00175000 2025-06-10 15:36:10+00:00   175.0       0.38    0.36   
35  NVDA250718C00180000 2025-06-10 15:37:23+00:00   180.0       0.23    0.24   
36  NVDA250718C00185000 2025-06-10 15:31:53+00:00   185.0       0.18    0.17   
37  NVDA250718C00190000 2025-06-10 15:55:08+00:00   190.0       0.14    0.12   
38  NVDA250718C00195000 2025-06-10 15:05:31+00:00   195.0       0.10    0.09   
39  NVDA250718C00200000 2025-06-10 15:30:06+00:00   200.0       0.09    0.08   
40  NVDA250718C00210000 2025-06-10 15:29:50+00:00   210.0       0.05    0.05   
41  NVDA250718C00220000 2025-06-10 15:55:34+00:00   220.0       0.03    0.03   
42  NVDA250718C00230000 2025-06-10 13:58:44+00:00   230.0       0.02    0.02   
43  NVDA250718C00240000 2025-06-10 13:30:00+00:00   240.0       0.02    0.02   
44  NVDA250718C00250000 2025-06-10 13:30:02+00:00   250.0       0.02    0.02   
45  NVDA250718C00260000 2025-06-09 19:01:23+00:00   260.0       0.02    0.01   
46  NVDA250718C00270000 2025-06-09 13:31:10+00:00   270.0       0.01    0.01   
47  NVDA250718C00280000 2025-06-10 14:14:09+00:00   280.0       0.01    0.00   
48  NVDA250718C00290000 2025-06-09 14:43:51+00:00   290.0       0.01    0.00   
49  NVDA2

## **Formatted Preview – Call Option Chain (Top 5)**

This step presents a **clean and structured overview** of the first 5 call option records for the selected expiration date of `NVDA`.

---

### **Displayed Columns**

| Field               | Description                                         |
|--------------------|-----------------------------------------------------|
| **Contract**        | Unique symbol representing the option contract      |
| **Strike Price**    | The agreed price at which the stock can be bought  |
| **Last Price**      | Most recent trading price of the option             |
| **Bid / Ask**       | Current market bid and ask prices                   |
| **Volume**          | Number of contracts traded on the current day       |
| **Implied Volatility** | Market expectation of future volatility (%)    |

---

### **Objective**

- To **quickly inspect** call options and get a feel for market pricing.
- To prepare for **filtering, visualization, or further modeling**.
- To help select strike prices for advanced strategies (e.g., vertical spreads, covered calls).

---

### **Technical Enhancements**

- The displayed DataFrame is styled using `pandas Styler` to:
  - Align values centrally
  - Format numerical values with consistent decimal places and percentage format for volatility
  - Rename columns for clarity

---

In [69]:
# Display formatted header
print("🎯 Sample Call Option Data (Selected Expiration):")

# Columns to Display
call_display_cols = {
    'contractSymbol': 'Contract',
    'strike': 'Strike Price',
    'lastPrice': 'Last Price',
    'bid': 'Bid',
    'ask': 'Ask',
    'volume': 'Volume',
    'impliedVolatility': 'Implied Volatility'
}

# Format and Display DataFrame
try:
    sample_calls = c[list(call_display_cols.keys())].head()
    sample_calls.rename(columns=call_display_cols, inplace=True)
    display(HTML("<b>📊 First 5 Call Option Records:</b>"))
    display(sample_calls.style.format({
        'Strike Price': '{:.2f}',
        'Last Price': '{:.2f}',
        'Bid': '{:.2f}',
        'Ask': '{:.2f}',
        'Implied Volatility': '{:.2%}'
    }).set_properties(**{'text-align': 'center'}).set_table_styles([{
        'selector': 'th', 'props': [('text-align', 'center')]
    }]))
except Exception as e:
    print(f"❌ Display error: {e}")


🎯 Sample Call Option Data (Selected Expiration):


## **Option Chain Visualization – Last Price vs. Strike Price**

This section provides a **multi-expiration visualization** of **call option chains** for the selected underlying asset: `NVDA`. The goal is to explore how **option premiums (last prices)** vary across different **strike prices and expiration dates**.

---

### **What This Chart Shows**

- **X-axis**: Strike prices of NVDA call options.  
- **Y-axis**: Corresponding **last traded prices** of each option.  
- **Lines**: Each line represents one expiration date's option chain.  
- **Interactive Hover**: Shows precise values for each contract (expiration, strike, last price).

---

### **Technical Details**

- **Primary Expiration**: The base contract (index 5) is plotted prominently.  
- **Dynamic Range**: If more expiration dates exist, additional ones are looped in and visualized.  
- **Hover Template**: Custom-designed for clarity with price formatting and full expiration info.

---

### **Additional Data Processing**

After plotting, all retrieved call option chains are:
- **Combined into one DataFrame**: `all_calls`  
- **Converted into datetime** for the `expiration` field  
- **Days to expiry** calculated for each contract  
- **MidPrice** estimated as the average of bid and ask prices

---

In [70]:
# Plotly Visualization: Option Chain by Expiration

print(f"\n📊 Creating Option Chain Visualization for {TICKER_SYMBOL}...")

# Initialize figure
fig = go.Figure()

# Plot the Base Expiration (Index 5)
try:
    base_call = ticker.option_chain(expirations[5]).calls
    fig.add_trace(go.Scatter(
        x=base_call.strike,
        y=base_call.lastPrice,
        mode='lines+markers',
        name=f"Base: {expirations[5]}",
        hovertemplate='<b>Expiration:</b> %{fullData.name}<br>' +
                      '<b>Strike:</b> %{x}<br>' +
                      '<b>Last Price:</b> %{y:.2f}<extra></extra>'
    ))
except Exception as e:
    print(f"⚠️ Could not plot base expiration {expirations[5]}: {e}")

# Determine Expirations to Loop Through
if 'selected_expirations_for_loop' not in locals():
    if len(expirations) >= 8:
        selected_expirations_for_loop = expirations[6:-2]
    elif len(expirations) > 6:
        selected_expirations_for_loop = expirations[6:]
    else:
        selected_expirations_for_loop = []
        print(f"⚠️ Not enough expiration dates for loop. Found: {len(expirations)}")

# Plot Remaining Expirations
option_chain_dataframes = []  # Initialize if not done before

for exp in selected_expirations_for_loop:
    try:
        call_data = ticker.option_chain(exp).calls
        if not call_data.empty:
            call_data['expiration'] = exp  # For later merging
            option_chain_dataframes.append(call_data)

            fig.add_trace(go.Scatter(
                x=call_data.strike,
                y=call_data.lastPrice,
                mode='lines+markers',
                name=exp,
                hovertemplate='<b>Expiration:</b> %{fullData.name}<br>' +
                              '<b>Strike:</b> %{x}<br>' +
                              '<b>Last Price:</b> %{y:.2f}<extra></extra>'
            ))
        else:
            print(f"⚠️ No call data for {exp}.")
    except Exception as e:
        print(f"❌ Error processing {exp}: {e}")
        continue



# Final Plot Layout (Improved)
fig.update_layout(
    title=dict(
        text=f"<b>{TICKER_SYMBOL} Call Options</b><br><span style='font-size:13px'>Last Price vs Strike for Selected Expirations</span>",
        x=0.5,  # Center the title
        font=dict(size=20)  # Main title font size
    ),
    xaxis_title="Strike Price",
    yaxis_title="Last Price",
    hovermode="x unified",
    template="plotly_white",
    margin=dict(l=40, r=40, t=100, b=60),  # Increased top margin for better spacing
    legend=dict(
        orientation="h",
        yanchor="top",
        y=-0.15,  # Move legend below the chart
        xanchor="center",
        x=0.5
    )
)

fig.show()

# Combine All Option Data into Single DataFrame
if option_chain_dataframes:
    all_calls = pd.concat(option_chain_dataframes, axis=0)
    all_calls['expiration'] = pd.to_datetime(all_calls['expiration'])
    all_calls['days_to_expiry'] = (all_calls['expiration'] - pd.Timestamp.now()).dt.days
    all_calls['midPrice'] = (all_calls['ask'] + all_calls['bid']) / 2

    print("\n✅ Combined Call Options Data (First 5 Rows):")
    display(all_calls[['contractSymbol', 'expiration', 'strike', 'midPrice', 'lastPrice', 'volume', 'impliedVolatility']].head())
else:
    print("\n⚠️ No option chain data collected. 'all_calls' is empty.")
    all_calls = pd.DataFrame()



📊 Creating Option Chain Visualization for NVDA...



✅ Combined Call Options Data (First 5 Rows):


contractSymbol expiration  strike  midPrice  lastPrice  volume  \
0  NVDA250725C00100000 2025-07-25   100.0    43.800      42.23     1.0   
1  NVDA250725C00105000 2025-07-25   105.0    38.900      38.83     3.0   
2  NVDA250725C00110000 2025-07-25   110.0    33.800      33.60     3.0   
3  NVDA250725C00111000 2025-07-25   111.0    33.050      31.59     1.0   
4  NVDA250725C00112000 2025-07-25   112.0    31.675      31.42    16.0   

   impliedVolatility  
0           0.610844  
1           0.561528  
2           0.532964  
3           0.503423  
4           0.518071

## **Implied Volatility vs. Strike Price (per Expiration)**

This visualization provides insight into how **Implied Volatility (IV)** varies across different **strike prices** and **option expiration dates** for the selected underlying asset: `NVDA`.

---

### **What the Chart Shows**

- **X-axis**: Strike Prices  
- **Y-axis**: Implied Volatility (decimal format; e.g., 0.40 = 40%)  
- **Color**: Distinct expiration dates (each shown as a different color)  
- **Hover Info**: Includes contract symbol, last price, mid price, and volume for detailed inspection

---

### **Purpose and Use Cases**

- Identify **volatility skews** across different strike levels
- Compare **IV surfaces** by maturity dates
- Spot anomalies or mispriced options  
- Serve as input for volatility models or trading strategies (e.g., calendar spreads, straddles, vertical spreads)

---

### **Data Filtering**

Only records with valid (`non-null`) values for both `impliedVolatility` and `strike` are included in the visualization to ensure data reliability.

---

In [71]:
# Filter: only valid implied volatility and strike data
filtered_calls = all_calls.dropna(subset=['impliedVolatility', 'strike'])

# Graph: IV vs Strike
fig_iv = px.scatter(
    filtered_calls,
    x='strike',
    y='impliedVolatility',
    color='expiration',
    hover_data=['contractSymbol', 'lastPrice', 'midPrice', 'volume'],
    title=f"{TICKER_SYMBOL} - Implied Volatility vs Strike by Expiration",
    labels={
        'strike': 'Strike Price',
        'impliedVolatility': 'Implied Volatility',
        'expiration': 'Expiration Date'
    },
    template='plotly_white'
)

fig_iv.update_layout(
    title=dict(
        x=0.5,
        font=dict(size=18)
    ),
    margin=dict(l=40, r=40, t=80, b=60),
    legend=dict(
        orientation="h",
        yanchor="top",
        y=-0.2,
        xanchor="center",
        x=0.5
    )
)

fig_iv.show()


## **3D Visualization: Option Prices by Strike & Time to Expiry**

This interactive 3D plot provides a comprehensive view of **Call Option Prices** for `NVDA`, segmented by **Strike Price**, **Days Until Expiry**, and **Last Traded Price**.

---

### **Axes Representation**

- **X-axis**: Days Remaining Until Option Expiry  
- **Y-axis**: Strike Price (in USD)  
- **Z-axis**: Last Traded Price of the Call Option  

The color gradient represents the number of days to expiry, enhancing the spatial separation of short- and long-term maturities.

---

### **Insights and Applications**

- **Volatility Surface Intuition**: Observe how price sensitivity shifts across different strike/maturity combinations.
- **Skew Detection**: Identify **volatility skew** and **pricing anomalies** visually.
- **Strategic Planning**: Aid in constructing **multi-leg strategies** like calendar spreads, strangles, or ladder trades.

---

### **Hover Data (Per Data Point)**

- **Contract Symbol**
- **Strike Price** (`$`)
- **Last Price** (`$`)
- **Expiration Date**
- **Days to Expiry**
- **Volume**
- **Implied Volatility (%)**

---

In [72]:
# 3D Scatter Plot: Option Prices by Strike and Time to Maturity

if not all_calls.empty:
    fig = px.scatter_3d(
        all_calls,
        x='days_to_expiry',
        y='strike',
        z='lastPrice',
        color='days_to_expiry',
        color_continuous_scale='Viridis',
        title=f'{TICKER_SYMBOL} Option Prices by Days to Expiry & Strike Price',
        labels={
            'days_to_expiry': 'Days Until Expiry',
            'strike': 'Strike Price ($)',
            'lastPrice': 'Last Price ($)'
        },
        hover_data={
            'days_to_expiry': True,
            'strike': ':.2f',
            'lastPrice': ':.2f',
            'expiration': True,
            'impliedVolatility': ':.2%',
            'volume': True,
            'contractSymbol': True
        }
    )

    # Update marker appearance
    fig.update_traces(marker=dict(size=4, opacity=0.85))

    # Update layout for enhanced 3D visualization
    fig.update_layout(
        template='plotly_white',
        title_font_size=20,
        scene=dict(
            xaxis=dict(
                title='Days to Expiry',
                backgroundcolor='whitesmoke',
                gridcolor='lightgrey',
                showbackground=True
            ),
            yaxis=dict(
                title='Strike Price ($)',
                backgroundcolor='whitesmoke',
                gridcolor='lightgrey',
                showbackground=True
            ),
            zaxis=dict(
                title='Last Price ($)',
                backgroundcolor='whitesmoke',
                gridcolor='lightgrey',
                showbackground=True
            ),
            bgcolor='white'
        ),
        margin=dict(l=0, r=0, t=60, b=0)
    )

    fig.show()

else:
    print("⚠️ Cannot plot: 'all_calls' DataFrame is empty.")


## **3D Option Price Surface Plot – Strike vs Days to Expiry**

This 3D surface visualization illustrates the **last traded price** of call options on `NVDA`, plotted against **Strike Price** and **Days Remaining Until Expiration**. The surface provides a smooth, continuous overview of option pricing behavior across the term structure and moneyness levels.

---

### **Plot Axes**

- **X-axis**: Strike Price (USD)  
- **Y-axis**: Time to Maturity (Days to Expiry)  
- **Z-axis**: Last Traded Option Price (USD)  

Color intensity on the surface reflects the option price level, with **Cividis** colormap enhancing contrast.

---

### **Strategic Applications**

- **Volatility & Price Surface Mapping**: Helps assess how option prices behave over different maturities and strike levels.
- **Identifying Mispricing**: Sudden dips or ridges in the surface may point to arbitrage opportunities or market inefficiencies.
- **Model Validation**: Compare against theoretical models (e.g., Black-Scholes or local volatility surfaces).

---

### **Hover Data Per Point**

- **Strike Price**
- **Days to Expiry**
- **Last Traded Price**

Each point on the surface represents the average last traded price for a given strike and expiration pairing, providing a clean snapshot of the live options market structure.

---

In [73]:
# 3D Surface Plot: Option Prices by Days to Expiry and Strike Price

if 'all_calls' in locals() and not all_calls.empty:
    required_cols = ['days_to_expiry', 'strike', 'lastPrice']

    if all(col in all_calls.columns for col in required_cols):
        pivot_table = all_calls.pivot_table(
            index='days_to_expiry',
            columns='strike',
            values='lastPrice',
            aggfunc='mean'
        )

        X = pivot_table.columns.values           # Strike Prices
        Y = pivot_table.index.values             # Days to Expiry
        Z = pivot_table.values                   # Last Prices (z-axis)

        fig = go.Figure(data=[
            go.Surface(
                x=X,
                y=Y,
                z=Z,
                colorscale='Cividis',
                colorbar_title='Option Price ($)',
                hovertemplate='<b>Strike Price:</b> %{x:.2f}<br>' +
                              '<b>Days to Expiry:</b> %{y}<br>' +
                              '<b>Last Price:</b> %{z:.2f}<extra></extra>',
                contours=dict(
                    z=dict(show=True, usecolormap=True,
                           highlightcolor="limegreen", project_z=True)
                )
            )
        ])

        fig.update_layout(
            title=f'{TICKER_SYMBOL} Option Surface: Last Price by Strike & Time to Maturity',
            scene=dict(
                xaxis=dict(title='Strike Price ($)', gridcolor='lightgrey', zerolinecolor='gray'),
                yaxis=dict(title='Days Until Expiry', gridcolor='lightgrey', zerolinecolor='gray'),
                zaxis=dict(title='Last Price ($)', gridcolor='lightgrey', zerolinecolor='gray'),
                bgcolor='white'
            ),
            template='plotly_white',
            title_font_size=20,
            margin=dict(l=0, r=0, t=60, b=0)
        )

        fig.show()
    else:
        print("⚠️ Surface plot failed: One or more required columns missing in 'all_calls'.")
else:
    print("⚠️ Surface plot failed: 'all_calls' DataFrame is empty or undefined.")


# **Portfolio Analysis**
In this section, we will analyse the performance of a portfolio consisting of multiple stocks over time. The following subheadings can be arranged in a professional analysis structure.

---

## **Total Wealth Evaluation (2015–2025)**

This section presents a **dynamic portfolio valuation model** built on historical daily closing prices of selected tech stocks, spanning from **January 1, 2015 to June 5, 2025**.

---

### **Assets Included:**
- **NVIDIA (NVDA)**
- **Microsoft (MSFT)**
- **Intel (INTC)**
- **Advanced Micro Devices (AMD)**
- **Adobe (ADBE)**

These equities represent a diversified exposure to the global semiconductor and software ecosystem.

---

### **Methodology Overview**

1. **Adjusted Close Prices**  
   Historical price data is fetched using the `yfinance` library, with `auto_adjust=True` to account for corporate actions (splits/dividends).

2. **Daily Simple Returns**  
   Percentage change between consecutive days provides insight into each asset's return behavior.

3. **Quantity Assignment**  
   A static investment strategy is assumed:
   - NVDA → 1 share
   - MSFT → 2 shares
   - INTC → 3 shares
   - AMD → 4 shares
   - ADBE → 5 shares

4. **Holding Value Computation**  
   Daily portfolio value is calculated by multiplying each stock's price by its assigned quantity.

5. **Total Portfolio Wealth**  
   The total wealth over time is derived by summing the holding values across all tickers on each date.

---

### **Visualization – Wealth Curve**

The resulting **wealth time series** plot illustrates the **growth and fluctuations** in the total portfolio value over the 10+ year horizon. This helps:

- Assess long-term growth performance
- Identify key volatility zones (crisis periods, rallies)
- Serve as a base for further risk and attribution analysis

---

### **Sample Outputs:**

- `prices.head()` → first rows of adjusted prices  
- `simple_returns.head()` → daily return preview  
- `quantities` → investment structure  
- `holding_values.head()` → position valuation  
- `total_wealth` → historical wealth vector  

---

In [74]:
# Configuration
tickers = ["NVDA", "MSFT", "INTC", "AMD", "ADBE"]
start_date = "2015-01-01"
end_date = "2025-06-06"
interval = "1d"

print(f"📥 Downloading adjusted close prices for {tickers} ({start_date} → {end_date})...")
data = yf.download(tickers, start=start_date, end=end_date, interval=interval, auto_adjust=False)
prices = data['Adj Close'].dropna()
print(f"✅ Data shape: {prices.shape}")

# Calculate Returns
pct_returns = prices.pct_change().dropna()

# Define Fixed Quantities
quantities = pd.DataFrame({'Quantity': [1, 2, 3, 4, 5]}, index=prices.columns)

# Compute Holding Values
holding_values = prices.multiply(quantities['Quantity'], axis=1)

# Compute Total Portfolio Value
total_wealth = holding_values.sum(axis=1)

# Display Tabular Summary
eda_tabs = {
    "📘 Adjusted Close Prices": prices,
    "📈 Daily Simple Returns": pct_returns,
    "📦 Holding Values": holding_values,
    "💰 Portfolio Wealth": total_wealth.to_frame(name="Total Wealth")
}

tab_contents = []
tab_titles = []

for label, df in eda_tabs.items():
    output = widgets.Output()
    with output:
        display(Markdown(f"## 🔍 {label}"))
        display(df.head())
        display(Markdown("---"))
        display(df.tail())
    tab_contents.append(output)
    tab_titles.append(label)

tabs = widgets.Tab(children=tab_contents)
for i, title in enumerate(tab_titles):
    tabs.set_title(i, title)

display(Markdown("## 📂 Portfolio Analysis: Tabular Summary"))
display(tabs)

# Visualization: Portfolio Wealth Over Time
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=total_wealth.index,
    y=total_wealth,
    mode='lines',
    name='Total Wealth',
    line=dict(color='green', width=2),
    hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Wealth:</b> %{y:.2f}<extra></extra>'
))

fig.update_layout(
    title='📊 Total Portfolio Wealth Over Time',
    xaxis_title='Date',
    yaxis_title='Total Wealth ($)',
    template='plotly_white',
    hovermode='x unified',
    margin=dict(l=0, r=0, t=50, b=0)
)

fig.show()


[**********************80%*************          ]  4 of 5 completed

📥 Downloading adjusted close prices for ['NVDA', 'MSFT', 'INTC', 'AMD', 'ADBE'] (2015-01-01 → 2025-06-06)...


[*********************100%***********************]  5 of 5 completed

✅ Data shape: (2622, 5)


## 📂 Portfolio Analysis: Tabular Summary

## **Scatter Plot Analysis: Return Relationship between NVDA and INTC**

This section presents a **bivariate scatter plot** to visually analyze the relationship between the daily simple returns of two major semiconductor stocks: **NVIDIA (NVDA)** and **Intel (INTC)**.

### **Methodology:**

- The daily return values for both `NVDA` and `INTC` are sourced from the previously computed `simple_returns` DataFrame.
- Each data point represents one trading day and is colored based on the **sign (direction) of Intel's return**:
  - 🟢 **Positive INTC Return**
  - 🔴 **Negative INTC Return**
  - ⚫ **Zero INTC Return**
- This classification allows us to quickly detect if there are directional co-movements between the two assets.

### **Insights Provided:**

- Whether NVDA tends to move in the same direction as INTC (positive correlation),
- How often they diverge in performance (opposing signs),
- Cluster behaviors around zero returns or extreme values.

### **Visual Output:**

The interactive scatter plot provides:
- Tooltips with exact return values for both stocks,
- Color-coded regions by INTC’s return sign,
- Clear axis labels and a descriptive plot title.

---

This type of visual analysis can be useful for **pair trading strategies**, **correlation estimation**, or simply understanding **return dependencies** between assets in the same sector.

---

In [75]:
ticker1 = 'NVDA'
ticker2 = 'INTC'

# Sanity Check
if ticker1 not in pct_returns.columns or ticker2 not in pct_returns.columns:
    raise ValueError(f"❌ '{ticker1}' or '{ticker2}' not found in return data.")

# Classify Return Sign Based on ticker2
print(f"\n📊 Categorizing return sign based on {ticker2}...")
return_label_col = f'{ticker2}_Return_Sign'
pct_returns[return_label_col] = pct_returns[ticker2].apply(
    lambda x: f'Positive {ticker2} Return' if x > 0 else
              (f'Negative {ticker2} Return' if x < 0 else f'Zero {ticker2} Return')
)

# Define Color Mapping
unique_labels = pct_returns[return_label_col].unique()
color_map = {
    f'Positive {ticker2} Return': 'green',
    f'Negative {ticker2} Return': 'red',
    f'Zero {ticker2} Return': 'grey'
}

# Build Title
plot_title = f"Scatter Plot of Daily Returns:\n{ticker1} vs. {ticker2} (Colored by {ticker2} Return Sign)"
wrapped_title = "<br>".join(textwrap.wrap(plot_title, width=60))

# Plot with Plotly Express
fig = px.scatter(
    pct_returns,
    x=ticker1,
    y=ticker2,
    color=return_label_col,
    color_discrete_map=color_map,
    opacity=0.7,
    hover_name=pct_returns.index,
    hover_data={
        ticker1: ':.4f',
        ticker2: ':.4f',
        return_label_col: False
    },
    labels={
        ticker1: f'{ticker1} Daily Returns',
        ticker2: f'{ticker2} Daily Returns',
        return_label_col: f'{ticker2} Return Sign'
    },
    title=wrapped_title
)

# Update Layout
fig.update_layout(
    template='plotly_white',
    title_font_size=18,
    hovermode='closest',
    xaxis_title=f'{ticker1} Daily Returns',
    yaxis_title=f'{ticker2} Daily Returns',
    legend_title_text=f'{ticker2} Return Sign',
    margin=dict(l=0, r=0, t=80, b=0)
)

# Show
fig.show()



📊 Categorizing return sign based on INTC...


## **Area Chart: Individual Asset Contributions to Portfolio Value**

This visualization illustrates the **evolution of the dollar value held in each stock over time** within the portfolio. It provides a stacked area chart where each layer represents the value contribution of a specific stock.

---

### **Methodology:**

- The dataset used is `holding_values`, which contains the dollar value of each asset (calculated as: *price × fixed quantity*).
- The data is reshaped using `pandas.melt()` to convert the wide-format DataFrame into a long-format structure required for area plotting.

---

### **Chart Features:**

- **X-axis** represents time (daily intervals from 2015 to 2025),
- **Y-axis** shows the cumulative dollar value contributed by each asset,
- **Colors** differentiate the individual stocks using a visually soft and professional `Set2` palette,
- **Hover tooltips** display exact dates and value amounts for better interactivity and readability.

---

### **Interpretation:**

- You can assess **which stocks contributed most** to the total portfolio value over time,
- Understand the **relative growth or decline** of specific holdings,
- Spot periods of strong stock-specific performance or decline (e.g., large shifts in NVDA or AMD during certain years).

---

This plot is essential for **portfolio composition analysis**, **performance attribution**, and **historical asset dominance evaluation**.

---

In [76]:
# Validate Data

## Use holding_values which was calculated in a previous cell
if holding_values.empty:
    raise ValueError("❌ 'holding_values' (holding values) is empty. Make sure you calculated holdings correctly.")

# Prepare Area Plot DataFrame
## Use holding_values instead of P_times_v
df_area = holding_values.copy()
df_area['Date'] = df_area.index
df_area = df_area.reset_index(drop=True)
df_area = df_area.melt(id_vars='Date', var_name='Stock', value_name='Holding Value ($)')

# Create Area Chart
fig = px.area(
    df_area,
    x='Date',
    y='Holding Value ($)',
    color='Stock',
    title='📊 Individual Stock Value Contributions Over Time',
    labels={
        'Date': 'Date',
        'Holding Value ($)': 'Holding Value ($)',
        'Stock': 'Stock Symbol'
    },
    hover_data={
        'Date': '|%Y-%m-%d',
        'Holding Value ($)': ':.2f'
    },
    color_discrete_sequence=px.colors.qualitative.Set2  # Softer professional palette
)

# Layout Customization
fig.update_layout(
    template='plotly_white',
    title_font=dict(size=22, family='Arial', color='black'),
    xaxis_title='Date',
    yaxis_title='Total Holding Value ($)',
    xaxis_tickformat='%Y-%m',
    hovermode='x unified',
    margin=dict(l=20, r=20, t=70, b=40),
    legend=dict(
        orientation='h',
        yanchor='bottom',
        y=1.02,
        xanchor='right',
        x=1
    ),
    legend_title_text='Stock Ticker'
)

# Line & Area Style Enhancements
fig.update_traces(
    line=dict(width=0.8),
    mode='lines'
)

# Show Plot
fig.show()


## **Stock Price Simulation Using Geometric Brownian Motion (GBM)**

Before simulating stock price paths using stochastic processes like Geometric Brownian Motion (GBM), it is important to understand and verify the behavior of random number generators across various probability distributions. These distributions serve as the foundation for Monte Carlo methods and stochastic differential equation solvers.

---

## **Histogram of Pseudo-Random Numbers (Normal Distribution)**

This section demonstrates how to generate and visualize pseudo-random numbers drawn from various probability distributions using NumPy’s random number generators. The histogram below focuses on the **Normal distribution** with a mean of 0 and standard deviation of 0.5.

### **Distributions Generated:**

A sample of 100,000 values was drawn from each of the following distributions:
- **Uniform (0,1)** – `rn.rand()`, `rn.uniform()`
- **Standard Normal** – `rn.randn()`
- **Beta(α=2, β=5)** – `rn.beta()`
- **Binomial(n=20, p=0.5)** – `rn.binomial()`
- **Chi-square (df=4)** – `rn.chisquare()`
- **Exponential (λ=1)** – `rn.exponential()`
- **Log-normal (μ=0, σ=0.5)** – `rn.lognormal()`
- **Normal (μ=0, σ=0.5)** – `rn.normal()`

### **Plot Details:**

- **Distribution Shown:** Normal(0, 0.5)
- **Tool Used:** Plotly Express for interactive and high-quality visualizations
- **Customizations:**
  - 100 bins for high granularity
  - Bar borders added for enhanced readability
  - Clean, minimal layout using `plotly_white` template

### **Interpretation:**

- The bell-shaped curve reflects the expected structure of a **Normal distribution**.
- The peak is centered around 0, with most values within ±1 standard deviation.
- This plot can be used to validate the shape and range of synthetic data used in **Monte Carlo simulations**, **option pricing**, or **stochastic modeling**.

---

> This kind of visual validation is essential before using generated numbers in quantitative finance or risk modeling tasks.
---

In [77]:
# Setting the seed (for reproducibility)
rn.seed(100)

# Generating random numbers from different probability distributions
rnu = rn.rand(100000, 1)      # Uniform (0,1) distribution
rnn = rn.randn(100000, 1)     # Standard Normal distribution (mean=0, standard deviation=1)
rn1 = rn.beta(2, 5, (100000, 1)) # Beta(alpha=2, beta=5) distribution
rn2 = rn.binomial(20, 0.5, (100000, 1)) # Binomial(n=20, p=0.5) distribution
rn3 = rn.chisquare(4, (100000, 1)) # Chi-Square(df=4) distribution
rn4 = rn.exponential(scale=1, size=(100000, 1)) # Exponential(lambda=1) distribution
rn5 = rn.lognormal(mean=0, sigma=0.5, size=(100000, 1)) # Log-Normal(mean=0, std_dev=0.5) distribution
rn6 = rn.normal(loc=0, scale=0.5, size=(100000, 1)) # Normal(mean=0, std_dev=0.5) distribution
rn7 = rn.uniform(low=0, high=1, size=(100000, 1)) # Uniform (0,1) distribution (same as rn.rand)

# Plotting a histogram of one of the generated random numbers (using rn6)

# Create a Plotly Express histogram
fig = px.histogram(
    rn6,
    nbins=100,
    title='Histogram of Pseudo-Random Numbers (Normal Distribution)',
    labels={'value': 'Value', 'count': 'Frequency'},
    opacity=0.8,  # Increased opacity slightly
    color_discrete_sequence=['steelblue']
)

# Update layout for a professional look
fig.update_layout(
    template='plotly_white',
    title_font_size=20,
    xaxis_title_font_size=14,
    yaxis_title_font_size=14,
    bargap=0.05,
    margin=dict(l=0, r=0, t=50, b=0)
)

# Make bars more prominent by adding a border
fig.update_traces(
    marker=dict(
        line=dict(
            width=1,  # Border width
            color='DarkSlateGrey'  # Border color
        )
    )
)

# Show the interactive Plotly figure
fig.show()


## **Statistical Properties of Random Numbers: Techniques Comparison**

This analysis investigates how different **random number generation techniques** affect the **mean** and **standard deviation** of samples drawn from a standard normal distribution. The goal is to observe how statistical properties converge with increasing sample size and to evaluate variance reduction techniques.

---

### **1. Standard Random Number Generation**

Random numbers are drawn using `np.random.randn()`, which generates values from a standard normal distribution (μ=0, σ=1). As sample size increases (from 10¹ to 10⁷), we observe convergence of the sample mean and standard deviation to their theoretical values.

---

In [78]:
# Set the seed for reproducibility
rn.seed(100)

print("--- Analyzing Mean and Standard Deviation of Random Numbers ---")

# Standard Random Number Generation
print("\nGenerating and analyzing standard random numbers:")
for i in range(1, 8):
    # Generate 10^i standard normal random numbers
    num_samples = 10**i
    random_numbers = rn.randn(num_samples)

    # Calculate mean and standard deviation
    mean_val = np.mean(random_numbers)
    std_val = np.std(random_numbers)

    # Print formatted results
    print(f"Number of random numbers: {num_samples:9.0f} | Mean: {mean_val:.12f} | Standard deviation: {std_val:.12f}.")

# Random Number Generation using Antithetic Variates
print("\nGenerating and analyzing random numbers using Antithetic Variates:")
# Antithetic variates is a variance reduction technique.
# For each random number, its negative is also included.
rn.seed(100) # Reset seed for this section to compare from the same starting point
for i in range(1, 8):
    # Generate half the required number of random numbers
    num_samples_half = round(10**i / 2)
    random_half = rn.randn(num_samples_half)

    # Create antithetic variates by including the negatives
    antithetic_numbers = np.concatenate((random_half, -random_half))

    # Calculate mean and standard deviation of the combined set
    mean_val = np.mean(antithetic_numbers)
    std_val = np.std(antithetic_numbers)

    # Print formatted results
    print(f"Number of random numbers: {len(antithetic_numbers):9.0f} | Mean: {mean_val:.12f} | Standard deviation: {std_val:.12f}.")

# Random Number Generation using Moment Matching
print("\nGenerating and analyzing random numbers using Moment Matching:")
# Moment matching is a technique to adjust generated random numbers
# to exactly match the desired mean (0) and standard deviation (1).
rn.seed(100) # Reset seed for this section
for i in range(1, 8):
    # Generate 10^i standard normal random numbers
    num_samples = 10**i
    random_numbers = rn.randn(num_samples)

    # Apply moment matching:
    # Subtract the mean and divide by the standard deviation
    # This ensures the new set has mean 0 and standard deviation 1
    if np.std(random_numbers) > 0: # Avoid division by zero if all numbers are the same (unlikely with randn)
         moment_matched_numbers = (random_numbers - np.mean(random_numbers)) / np.std(random_numbers)
    else:
         moment_matched_numbers = random_numbers - np.mean(random_numbers) # Just center if std dev is zero

    # Calculate mean and standard deviation of the moment-matched set
    mean_val = np.mean(moment_matched_numbers)
    std_val = np.std(moment_matched_numbers)

    # Print formatted results
    print(f"Number of random numbers: {len(moment_matched_numbers):9.0f} | Mean: {mean_val:.12f} | Standard deviation: {std_val:.12f}.")

print("\n--- Analysis Complete ---")


--- Analyzing Mean and Standard Deviation of Random Numbers ---

Generating and analyzing standard random numbers:
Number of random numbers:        10 | Mean: 0.020569627676 | Standard deviation: 0.842042313297.
Number of random numbers:       100 | Mean: -0.173826616443 | Standard deviation: 0.994982483532.
Number of random numbers:      1000 | Mean: -0.003117544049 | Standard deviation: 1.038720025481.
Number of random numbers:     10000 | Mean: 0.000741772285 | Standard deviation: 1.002159818386.
Number of random numbers:    100000 | Mean: 0.002248399090 | Standard deviation: 0.995990272623.
Number of random numbers:   1000000 | Mean: -0.000090243735 | Standard deviation: 0.998491032509.
Number of random numbers:  10000000 | Mean: -0.000278756647 | Standard deviation: 0.999713136376.

Generating and analyzing random numbers using Antithetic Variates:
Number of random numbers:        10 | Mean: 0.000000000000 | Standard deviation: 1.052170620285.
Number of random numbers:       100 |

## **Geometric Brownian Motion (GBM) Simulation & Analysis**

This simulation models the evolution of asset prices using the **Geometric Brownian Motion (GBM)** process, which is widely used in financial engineering, especially for stock price modeling and option pricing under the Black-Scholes framework.

---

### **Parameters Used**

| Parameter | Description              | Value     |
|-----------|--------------------------|-----------|
| μ (mu)    | Drift (Expected Return)  | 0.10      |
| σ (sigma) | Volatility               | 0.20      |
| S₀        | Initial Price            | 100       |
| T         | Time Horizon (years)     | 1         |
| dt        | Time Step                | 0.01      |
| N         | Number of Paths          | 10,000    |

---

### **Simulation Logic**

- The GBM model follows the stochastic differential equation (SDE):

  $$
  dS_t = \mu S_t \, dt + \sigma S_t \, dW_t
  $$

- Discretized version used in the simulation:

  $$
  S_{t+\Delta t} = S_t \cdot \exp\left[\left(\mu - \frac{1}{2}\sigma^2\right)\Delta t + \sigma \sqrt{\Delta t} \cdot Z_t\right]
  $$

  where \( Z_t \sim \mathcal{N}(0,1) \) are standard normal random variables.

- A total of **10,000 price paths** were simulated over **100 steps** (1 year with 0.01 increments).

---

### **Visualization Outputs**

- **First 10 Simulated Price Paths:**  
  Shows the stochastic nature of the GBM paths. Each path starts at $100 and evolves differently based on random shocks.

- **Histogram of Final Prices:**  
  Illustrates the **log-normal distribution** of terminal prices after 1 year. This is consistent with the theoretical properties of GBM.

---

### **Numerical Results**

| Metric                    | Value      |
|---------------------------|------------|
| Empirical Mean            | ≈ `μ_sim`  |
| Empirical Standard Dev.   | ≈ `σ_sim`  |
| Theoretical Mean          | $( S_0 e^{\mu T})$ |
| Theoretical Std. Dev.     | $( S_0 e^{\mu T} \sqrt{e^{\sigma^2 T} - 1} )$ |

The comparison between empirical and theoretical values confirms the accuracy of the simulation. As the number of trials increases, the convergence improves.

---

> GBM is the foundation of many pricing models. This simulation can be extended to compute derivative pricing (e.g., options), risk metrics (e.g., VaR), and Monte Carlo valuations.

---

In [79]:
# Geometric Brownian Motion (GBM) Simulation & Visualization

# Parameters
mu = 0.1             # Drift (Expected Return)
sigma = 0.2          # Volatility
S0 = 100             # Initial Price
T = 1                # Time Horizon (in years)
dt = 0.01            # Time Step
num_trials = 10_000  # Simulation Paths
num_steps = int(T / dt)

np.random.seed(100)  # Reproducibility

# GBM Simulation
print(f"Simulating {num_trials} GBM paths over {num_steps} steps...")

# Pre-allocate price matrix
stock_paths = np.zeros((num_trials, num_steps + 1))
stock_paths[:, 0] = S0

# Vectorized simulation
drift = (mu - 0.5 * sigma**2) * dt
diffusion = sigma * np.sqrt(dt)

Z = np.random.randn(num_trials, num_steps)  # Standard normal shocks
increments = drift + diffusion * Z
log_returns = np.cumsum(increments, axis=1)  # Cumulative log-returns
stock_paths[:, 1:] = S0 * np.exp(log_returns)

print("✅ Simulation complete.")

# Plot Simulated Price Paths
print(f"\n📊 Displaying first {min(10, num_trials)} GBM paths...")
time_grid = np.linspace(0, T, num_steps + 1)

fig_paths = go.Figure()

for i in range(min(10, num_trials)):
    fig_paths.add_trace(go.Scattergl(
        x=time_grid,
        y=stock_paths[i],
        mode='lines',
        name=f'Trial {i+1}',
        line=dict(width=1),
        hovertemplate='Time: %{x:.2f}<br>Price: %{y:.2f}<extra></extra>'
    ))

fig_paths.update_layout(
    title=f'GBM Simulation Paths (μ={mu}, σ={sigma}, S₀={S0})',
    xaxis_title='Time (Years)',
    yaxis_title='Simulated Price',
    template='plotly_white',
    margin=dict(l=0, r=0, t=60, b=0),
    hovermode='x unified',
    legend=dict(orientation='h', y=1.02, x=1, xanchor='right', yanchor='bottom')
)
fig_paths.show()

# Histogram of Final Prices
print("\n📊 Displaying histogram of final simulated prices...")
final_prices = stock_paths[:, -1]

fig_hist = px.histogram(
    final_prices,
    nbins=100,
    title=f'Distribution of Final Simulated Prices at T = {T} Year',
    labels={'value': 'Final Price', 'count': 'Frequency'},
    color_discrete_sequence=['darkorange'],
    opacity=0.75
)

fig_hist.update_layout(
    template='plotly_white',
    title_font_size=20,
    xaxis_title='Final Price',
    yaxis_title='Frequency',
    bargap=0.02,
    margin=dict(l=0, r=0, t=60, b=0)
)

fig_hist.update_traces(
    marker_line_width=1,
    marker_line_color='darkslategrey'
)

fig_hist.show()

# Numerical Analysis
print("\n📈 Statistical Analysis of Simulated Final Prices:")
empirical_mean = final_prices.mean()
empirical_std = final_prices.std()

theoretical_mean = S0 * np.exp(mu * T)
theoretical_std = S0 * np.exp(mu * T) * np.sqrt(np.exp(sigma**2 * T) - 1)

print(f"Empirical Mean       : {empirical_mean:.4f}")
print(f"Empirical Std Dev    : {empirical_std:.4f}")
print(f"Theoretical Mean      : {theoretical_mean:.4f}")
print(f"Theoretical Std Dev   : {theoretical_std:.4f}")
print("Note: Closer alignment is expected as trial count increases.")


Simulating 10000 GBM paths over 100 steps...
✅ Simulation complete.

📊 Displaying first 10 GBM paths...



📊 Displaying histogram of final simulated prices...



📈 Statistical Analysis of Simulated Final Prices:
Empirical Mean       : 110.5488
Empirical Std Dev    : 22.3115
Theoretical Mean      : 110.5171
Theoretical Std Dev   : 22.3263
Note: Closer alignment is expected as trial count increases.


## **Jump-Diffusion Model (Merton Model) Simulation Summary**

This simulation uses **Merton’s Jump-Diffusion Model**, which extends the Geometric Brownian Motion (GBM) by introducing **random jumps** in the price process.

### **Parameters:**

- Drift (μ): 0.1
- Volatility (σ): 0.2
- Initial Price (S₀): 100
- Time Horizon (T): 1 year
- Time Step (Δt): 0.01
- Number of Simulations: 10,000
- Jump Intensity (λ): 0.75 jumps/year
- Jump Size Mean (μ_j): -0.2 (in log-space)
- Jump Size Std Dev (σ_j): 0.1 (in log-space)

### **Model Equation (Discretized):**

Each price path is simulated according to:

$$
S_{t+\Delta t} = S_t \cdot \exp\left[(\mu - \frac{1}{2}\sigma^2)\Delta t + \sigma \sqrt{\Delta t} \cdot Z_t + Y_t\right]
$$

- $( Z_t \sim \mathcal{N}(0,1))$: standard Brownian noise  
- $( Y_t)$: compound jump term where the number of jumps follows a Poisson distribution $( J_t \sim \text{Poisson}(\lambda \cdot \Delta t))$ and jump sizes follow a normal distribution $( \mathcal{N}(\mu_j, \sigma_j^2))$

#### **Outputs:**

- First **10 simulation paths** plotted over time
- Histogram showing the distribution of **final prices at T = 1**
- Summary statistics:
  - **Mean Final Price**
  - **Standard Deviation of Final Price**

---

*Note:* This approach captures **rare, large changes** in stock prices, making it more realistic for markets prone to shocks or abrupt events.

---

In [80]:
# Parameters for Jump-Diffusion Model (Merton's Model)
mu = 0.1            # Drift
sigma = 0.2         # Volatility
S0 = 100            # Initial price
T = 1               # Time horizon (in years)
dt = 0.01           # Time step
num_trials = 10000  # Number of paths
jump_lambda = 0.75  # Jump intensity (average jumps per year)
jump_mu = -0.2      # Mean jump size (in log space)
jump_sigma = 0.1    # Standard deviation of jump size (in log space)

num_steps = int(T / dt)
time_grid = np.linspace(0, T, num_steps + 1)

np.random.seed(42)

# Initialize price matrix
S = np.zeros((num_trials, num_steps + 1))
S[:, 0] = S0

# Simulate jump diffusion paths
for t in range(1, num_steps + 1):
    Z = np.random.normal(0, 1, num_trials)
    J = np.random.poisson(jump_lambda * dt, num_trials)  # Jump count
    Y = np.random.normal(jump_mu, jump_sigma, num_trials) * J  # Jump size in log space
    drift = (mu - 0.5 * sigma**2) * dt
    diffusion = sigma * np.sqrt(dt) * Z
    S[:, t] = S[:, t-1] * np.exp(drift + diffusion + Y)

# Plot: Jump-Diffusion Paths
fig_jump = go.Figure()
for i in range(min(10, num_trials)):
    fig_jump.add_trace(go.Scatter(
        x=time_grid,
        y=S[i],
        mode='lines',
        name=f'Trial {i+1}',
        line=dict(width=1),
        hovertemplate='Time: %{x:.2f}<br>Price: %{y:.2f}<extra></extra>'
    ))

fig_jump.update_layout(
    title='Jump-Diffusion Simulated Price Paths (Merton Model)',
    xaxis_title='Time (Years)',
    yaxis_title='Stock Price',
    template='plotly_white',
    hovermode='x unified',
    margin=dict(l=0, r=0, t=60, b=0),
    legend=dict(orientation='h', y=1.02, x=1, xanchor='right', yanchor='bottom')
)

# Histogram of Final Prices
final_prices = S[:, -1]
fig_hist_jump = px.histogram(
    final_prices,
    nbins=100,
    title='Distribution of Final Prices under Jump-Diffusion',
    labels={'value': 'Final Price', 'count': 'Frequency'},
    color_discrete_sequence=['indigo'],
    opacity=0.75
)

fig_hist_jump.update_layout(
    template='plotly_white',
    title_font_size=20,
    xaxis_title='Final Price',
    yaxis_title='Frequency',
    margin=dict(l=0, r=0, t=60, b=0)
)

fig_hist_jump.update_traces(
    marker_line_width=1,
    marker_line_color='darkslategrey'
)

# Statistical Summary
mean_final = final_prices.mean()
std_final = final_prices.std()

summary_df = pd.DataFrame({
    'Metric': ['Mean Final Price', 'Std Dev Final Price'],
    'Value': [mean_final, std_final]
})

# Use standard display for the summary DataFrame
display(summary_df)

fig_jump.show()
fig_hist_jump.show()

Metric      Value
0     Mean Final Price  96.373327
1  Std Dev Final Price  25.660693

## **Ornstein–Uhlenbeck Process Simulation (Mean-Reverting Model)**

The **Ornstein–Uhlenbeck (OU)** process is a type of **mean-reverting stochastic process**, often used to model interest rates, commodity prices, and volatility in finance.

### **Model Dynamics:**

The continuous-time stochastic differential equation (SDE) for the OU process is:

$$
dX_t = \theta (\mu - X_t)dt + \sigma dW_t
$$

Where:
- $( \theta)$: speed of mean reversion
- $( \mu )$: long-term mean (reversion level)
- $( \sigma)$: volatility of the process
- $( dW_t )$: Wiener process increment (standard Brownian motion)

### **Simulation Parameters:**

- Speed of Reversion $( \theta )$: 0.15  
- Long-term Mean $( \mu )$: 100  
- Volatility $( \sigma )$: 0.3  
- Initial Value $( X_0 )$: 90  
- Time Horizon $( T )$: 1 year  
- Time Step $( \Delta t )$: 0.01  
- Number of Simulations: 10  

### **Output:**

The graph displays **10 independent OU paths**. Over time, these stochastic processes fluctuate and gradually revert toward the long-term mean $( \mu = 100 )$. The level of reversion depends on the parameter $( \theta )$; higher values cause faster convergence.

---

*Note:* This model is particularly relevant for financial applications where values tend to stabilize or revert around a long-run average.

---

In [81]:
# Ornstein-Uhlenbeck (Mean-Reverting) Process Parameters
theta = 0.15     # Speed of reversion
mu = 100         # Long-term mean
sigma = 0.3      # Volatility
X0 = 90          # Initial value
T = 1            # Time horizon (in years)
dt = 0.01        # Time step
num_paths = 10   # Number of paths to simulate
num_steps = int(T / dt)

# Set seed for reproducibility
np.random.seed(42)

# Simulate Ornstein-Uhlenbeck Process
X = np.zeros((num_paths, num_steps + 1))
X[:, 0] = X0

for t in range(1, num_steps + 1):
    dW = np.random.normal(0, np.sqrt(dt), size=num_paths)
    X[:, t] = X[:, t - 1] + theta * (mu - X[:, t - 1]) * dt + sigma * dW

# Time axis for plotting
time = np.linspace(0, T, num_steps + 1)

# Plot Simulated Paths
fig_ou = go.Figure()

for i in range(num_paths):
    fig_ou.add_trace(go.Scatter(
        x=time,
        y=X[i, :],
        mode='lines',
        name=f'Path {i+1}',
        line=dict(width=1),
        hovertemplate='<b>Time:</b> %{x:.2f}<br><b>Value:</b> %{y:.2f}<extra></extra>'
    ))

fig_ou.update_layout(
    title='Mean-Reverting Process (Ornstein–Uhlenbeck) Simulation',
    xaxis_title='Time (Years)',
    yaxis_title='Process Value',
    template='plotly_white',
    hovermode='closest',
    margin=dict(l=0, r=0, t=60, b=0),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)

fig_ou.show()


# **Time Series Analysis**

## **Advanced ARCH/GARCH Modeling & Simulation for Microsoft (NVDA)**

This notebook performs a comprehensive analysis of **Nvidia (NVDA)** stock returns using the **AR(1)-GARCH(1,1)** model with **Student's t-distribution**. The workflow includes model estimation, forward simulation, interactive visualization, and statistical diagnostics.

---

### **Methodological Workflow:**

#### 1. **Data Acquisition & Preprocessing**
- Historical NVDA data (2010–2025) is downloaded using `yfinance`.
- Log returns are calculated to ensure stationarity and model compatibility.

#### 2. **GARCH Model Specification**
- An **AR(1)** structure is used to model the mean.
- A **GARCH(1,1)** model is applied to the conditional variance.
- Residuals follow a **Student's t-distribution** to capture fat tails.

#### 3. **Simulation of Returns & Volatility**
- Future **1,000 daily returns** are simulated from the fitted model.
- Both return and volatility paths are generated using `arch_model.simulate`.

#### 4. **Visualization**
- **Plot 1:** Observed vs Simulated **Returns**  
- **Plot 2:** Observed vs Simulated **Conditional Volatility**  
Interactive plots are created using **Plotly**.

#### 5. **Statistical Diagnostics**
- Mean and standard deviation comparisons between observed and simulated data.
- **Jarque–Bera test** assesses the normality of returns.
- **Ljung–Box test** checks autocorrelation in standardized residuals.

---

### ⚙️ Key Parameters:
- Drift term: Estimated via AR(1)
- Volatility model: GARCH(1,1)
- Innovations: Student's t
- Simulation horizon: 1000 trading days
- Random seed: 100 (reproducibility ensured)

---

#### 🧪 Interpretation:
This model captures both **time-varying volatility** and **heavy tails**, which are characteristic of financial time series. Simulated outputs closely mirror real-world dynamics, making it suitable for **risk management**, **forecasting**, and **derivative pricing** applications.

---

In [82]:
# ADVANCED ARCH/GARCH SIMULATION & VISUALIZATION FOR NVDA
# Purpose: Model estimation, simulation & diagnostic of NVDA returns

# Configuration
TICKER = 'NVDA'
SIMULATION_PERIODS = 1000
RANDOM_STATE = 100

# Data Download And Log Return Calculation
def download_data(ticker, start, end):
    print(f"📥 Downloading data for {ticker} from {start} to {end}...")
    data = yf.download(ticker, start=start, end=end, auto_adjust=True)
    if data.empty or 'Close' not in data:
        raise ValueError("❌ Failed to retrieve valid 'Close' data.")
    log_returns = 100 * np.log(data['Close'] / data['Close'].shift(1)).dropna()
    print(f"✅ Data downloaded. Log returns shape: {log_returns.shape}")
    return log_returns

# Fit GARCH Model
def fit_garch_model(log_returns):
    print(f"\n⚙️ Estimating AR(1)-GARCH(1,1) model with Student's t distribution...")
    model = arch_model(log_returns, mean='AR', lags=1, vol='Garch', p=1, q=1, dist='StudentsT')
    results = model.fit(disp='off')
    print("✅ Model estimation complete.")
    print("\n📊 --- Model Summary ---")
    print(results.summary())
    print("-------------------------")
    return model, results

# Simulate Future Returns & Volatility
def simulate_returns(model, results, log_returns, periods):
    print(f"\n🔁 Simulating {periods} daily returns and volatility using fitted model...")
    sim_data = model.simulate(params=results.params,
                              nobs=periods,
                              initial_value=log_returns.iloc[-1])
    sim_index = pd.bdate_range(log_returns.index[-1], periods=periods + 1)[1:]
    sim_data.index = sim_index
    print("✅ Simulation complete.")
    print("\nSimulated Data Preview (Head):")
    print(sim_data.head())
    print("\nSimulated Data Preview (Tail):")
    print(sim_data.tail())
    return sim_data

# Plot Observed And Simulated Data
def plot_simulation(log_returns, results, sim_data, ticker):
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                        subplot_titles=(f"{ticker} Returns (Observed vs Simulated)",
                                        f"{ticker} Volatility (Observed vs Simulated)"))

    # Returns
    fig.add_trace(go.Scattergl(x=log_returns.index, y=log_returns.iloc[:, 0] if isinstance(log_returns, pd.DataFrame) else log_returns,
                               name="Observed Returns", line=dict(color='navy'),
                               hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Return:</b> %{y:.2f}%'),
                  row=1, col=1)
    fig.add_trace(go.Scattergl(x=sim_data.index, y=sim_data['data'],
                               name="Simulated Returns", line=dict(color='crimson'),
                               hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Return:</b> %{y:.2f}%'),
                  row=1, col=1)

    # Volatility
    fig.add_trace(go.Scattergl(x=log_returns.index, y=results.conditional_volatility,
                               name="Observed Volatility", line=dict(color='darkblue'),
                               hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Volatility:</b> %{y:.2f}%'),
                  row=2, col=1)
    fig.add_trace(go.Scattergl(x=sim_data.index, y=sim_data['volatility'],
                               name="Simulated Volatility", line=dict(color='firebrick'),
                               hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Volatility:</b> %{y:.2f}%'),
                  row=2, col=1)

    fig.update_layout(title=f"<b>ARCH/GARCH Model Estimation and Simulation for {ticker}</b>",
                      template='plotly_white', hovermode='x unified',
                      height=750,
                      margin=dict(l=40, r=40, t=80, b=40),
                      legend=dict(orientation="h", yanchor="bottom", y=1.04, xanchor="right", x=1))

    fig.update_xaxes(title_text="Date", row=2, col=1)
    fig.update_yaxes(title_text="Return (%)", row=1, col=1)
    fig.update_yaxes(title_text="Volatility (%)", row=2, col=1)

    fig.show()

# Statistical Diagnostics
def run_diagnostics(log_returns, sim_data, results):
    print("\n📈 --- Return & Volatility Comparison ---")
    log_returns_mean = log_returns.mean().iloc[0] if isinstance(log_returns, pd.DataFrame) else log_returns.mean()
    log_returns_std = log_returns.std().iloc[0] if isinstance(log_returns, pd.DataFrame) else log_returns.std()
    print(f"Observed Returns - Mean: {log_returns_mean:.4f}%, Std Dev: {log_returns_std:.4f}%")
    print(f"Simulated Returns - Mean: {sim_data['data'].mean():.4f}%, Std Dev: {sim_data['data'].std():.4f}%")

    print(f"Observed Volatility (Conditional) - Mean: {results.conditional_volatility.mean():.4f}%, Std Dev: {results.conditional_volatility.std():.4f}%")
    print(f"Simulated Volatility - Mean: {sim_data['volatility'].mean():.4f}%, Std Dev: {sim_data['volatility'].std():.4f}%")

    # Jarque-Bera Test
    jb_stat, jb_pval, _, _ = jarque_bera(log_returns)
    jb_stat_scalar = jb_stat[0] if isinstance(jb_stat, np.ndarray) else jb_stat
    jb_pval_scalar = jb_pval[0] if isinstance(jb_pval, np.ndarray) else jb_pval
    print(f"\n🧪 Jarque-Bera Test (Normality): JB = {jb_stat_scalar:.2f}, p = {jb_pval_scalar:.4f}")

    # Ljung-Box Test
    residuals = results.resid
    volatility = results.conditional_volatility
    standardized_resid = residuals / volatility
    lb_test = acorr_ljungbox(standardized_resid, lags=[10], return_df=True)
    print(f"\n🧪 Ljung-Box Test (Autocorrelation at Lag 10):")
    print(lb_test)
    print("Interpretation: p-values > 0.05 suggest no significant autocorrelation.")
    print("✅ Diagnostics complete.")

# Main Execution
log_returns = download_data(TICKER, START_DATE, END_DATE)
model, results = fit_garch_model(log_returns)
sim_data = simulate_returns(model, results, log_returns, SIMULATION_PERIODS)
plot_simulation(log_returns, results, sim_data, TICKER)
run_diagnostics(log_returns, sim_data, results)


[*********************100%***********************]  1 of 1 completed

📥 Downloading data for NVDA from 2020-01-01 to 2025-06-06...
✅ Data downloaded. Log returns shape: (1363, 1)

⚙️ Estimating AR(1)-GARCH(1,1) model with Student's t distribution...
✅ Model estimation complete.

📊 --- Model Summary ---
                              AR - GARCH Model Results                              
Dep. Variable:                         NVDA   R-squared:                       0.005
Mean Model:                              AR   Adj. R-squared:                  0.004
Vol Model:                            GARCH   Log-Likelihood:               -3506.24
Distribution:      Standardized Student's t   AIC:                           7024.48
Method:                  Maximum Likelihood   BIC:                           7055.78
                                              No. Observations:                 1362
Date:                      Tue, Jun 10 2025   Df Residuals:                     1360
Time:                              16:54:35   Df Model:                            2
 


📈 --- Return & Volatility Comparison ---
Observed Returns - Mean: 0.2314%, Std Dev: 3.4441%
Simulated Returns - Mean: 0.3165%, Std Dev: 3.4562%
Observed Volatility (Conditional) - Mean: 3.3617%, Std Dev: 0.8553%
Simulated Volatility - Mean: 3.3659%, Std Dev: 0.8894%

🧪 Jarque-Bera Test (Normality): JB = 822.49, p = 0.0000

🧪 Ljung-Box Test (Autocorrelation at Lag 10):
    lb_stat  lb_pvalue
10      NaN        NaN
Interpretation: p-values > 0.05 suggest no significant autocorrelation.
✅ Diagnostics complete.


## **Advanced GARCH(1,1) Modeling & 10-Day Volatility Forecast — NVDA**

This notebook demonstrates a full volatility modeling pipeline using **AR(1)-GARCH(1,1)** with **Student’s t-distribution** for **Nvidia (NVDA)** daily returns. The analysis includes model estimation, standardized residual diagnostics, volatility forecasting, and insightful visualizations.

---

### **Key Steps:**

#### 1. **Data Preparation**
- Historical daily closing prices from 2010 to 2025 are retrieved via `yfinance`.
- Returns are transformed into log-returns (percentage).

#### 2. **Model Estimation**
- The conditional mean is modeled with **AR(1)**.
- The conditional variance is modeled with **GARCH(1,1)**.
- Error distribution is set to **Student's t**, capturing heavy tails.

#### 3. **Residual Diagnostics**
- Standardized residuals are analyzed for:
  - **Skewness**, **kurtosis**, and **Jarque–Bera** normality test.
  - **Ljung–Box** test for autocorrelation in residuals and squared residuals.
  - **Histogram**, **ACF plots**, and **QQ-plot** (vs t-distribution) for visual diagnostics.

#### 4. **Forecasting Volatility**
- **10-step ahead volatility forecasts** are produced analytically.
- The last 10 days of observed conditional volatility are compared with forecasted values using interactive **Plotly** visualizations.

#### 5. **Visualization Outputs**
- ACF/PACF plots of residuals and squared residuals.
- Histogram and QQ-plot of standardized residuals.
- Time series plot comparing historical and forecasted volatility.

---

### **Model Configuration:**

| Parameter     | Value                          |
|---------------|---------------------------------|
| Ticker        | NVDA                            |
| Time Window   | 2010-01-01 to 2025-06-02        |
| Model         | AR(1) + GARCH(1,1)              |
| Distribution  | Student’s t-distribution        |
| Forecast      | 10 business days ahead          |

---

### **Interpretation:**
The model successfully captures the **volatility clustering** observed in financial returns. Diagnostic tests validate model assumptions, while the forecast provides practical insights for **risk management**, **option pricing**, and **portfolio volatility estimation**.

---

In [83]:
# Configuration
TICKER = 'NVDA'
FORECAST_HORIZON = 10

# Model Fitting
print("⚙️ Fitting AR(1)-GARCH(1,1) with Student's t-distribution...")
model = arch_model(log_returns, mean='AR', lags=1, vol='Garch', p=1, q=1, dist='StudentsT')
fitted = model.fit(disp='off')
print("✅ Model fitted.\n")
print(fitted.summary())

# # Residuals & Standardization
resid = fitted.resid
vol = fitted.conditional_volatility
std_resid = resid / (vol + 1e-12)
std_resid = std_resid.replace([np.inf, -np.inf], np.nan).dropna()

# Distributional Statistics
jb_stat, jb_pval, _, _ = jarque_bera(std_resid)

print("\n📊 Distributional Statistics:")
print(f"• Skewness: {skew(std_resid):.4f}")
print(f"• Kurtosis: {kurtosis(std_resid):.4f}")
print(f"• Jarque-Bera: JB = {jb_stat:.2f}, p = {jb_pval:.4f}")

# Interactive Histogram
fig_hist = px.histogram(std_resid, nbins=100,
                        title="📊 Histogram of Standardized Residuals",
                        labels={'value': 'Standardized Residual'},
                        template='plotly_white')
fig_hist.update_layout(xaxis_title='Standardized Residual', yaxis_title='Frequency')
fig_hist.show()

# Interactive ACF Plots
def plot_interactive_acf(series, lags=40, title="ACF Plot"):
    acf_vals = acf(series, nlags=lags, fft=True)
    fig = go.Figure()
    fig.add_trace(go.Bar(x=list(range(len(acf_vals))), y=acf_vals,
                         marker_color='royalblue'))
    fig.update_layout(title=title, xaxis_title='Lag', yaxis_title='ACF',
                      template='plotly_white')
    fig.show()

plot_interactive_acf(std_resid, title='📈 ACF of Standardized Residuals')
plot_interactive_acf(std_resid ** 2, title='📈 ACF of Squared Standardized Residuals')

# Interactive QQ Plots
fig = go.Figure()
if 'nu' in fitted.params:
    nu = fitted.params['nu']
    theoretical_quantiles, ordered_resid = probplot(std_resid, dist=student_t, sparams=(nu,), fit=False)
    qq_title = "📏 QQ Plot vs Student's t Distribution"
else:
    theoretical_quantiles, ordered_resid = probplot(std_resid, dist='norm', fit=False)
    qq_title = "📏 QQ-Plot vs Normal distribution"


fig.add_trace(go.Scatter(x=theoretical_quantiles, y=ordered_resid, mode='markers',
                         name='Data', marker=dict(color='teal')))
fig.add_trace(go.Scatter(x=theoretical_quantiles, y=theoretical_quantiles,
                         mode='lines', name='45° Line', line=dict(color='red', dash='dash')))
fig.update_layout(title=qq_title,
                  xaxis_title="Theoretical Quantiles", yaxis_title="Sample Quantiles",
                  template='plotly_white')
fig.show()


# L-Jung Box Tests
print("\n🧪 Ljung–Box Tests:")
for l in [10, 20, 30]:
    lb = acorr_ljungbox(std_resid, lags=[l], return_df=True)
    pval = lb['lb_pvalue'].values[0]
    print(f"  Lag {l}: p = {pval:.4f} ({'✅ no autocorrelation' if pval > 0.05 else '❌ autocorrelation present'})")

# Forecast
print(f"\n🔮 Forecasting {FORECAST_HORIZON}-day ahead volatility...")
forecast = fitted.forecast(horizon=FORECAST_HORIZON, method='analytic')
vol_forecast = forecast.variance.iloc[-1]**0.5
last_vol = fitted.conditional_volatility.iloc[-10:]

forecast_index = pd.bdate_range(log_returns.index[-1], periods=FORECAST_HORIZON+1)[1:]
forecast_df = pd.DataFrame({
    'Date': forecast_index,
    'Forecasted Volatility (%)': vol_forecast.values
})

# Interactive Forecast Chart
fig_vol = go.Figure()
fig_vol.add_trace(go.Scatter(x=last_vol.index, y=last_vol,
                             mode='lines', name='Observed Volatility', line=dict(color='blue')))
fig_vol.add_trace(go.Scatter(x=forecast_df['Date'], y=forecast_df['Forecasted Volatility (%)'],
                             mode='lines+markers', name='Forecasted Volatility', line=dict(color='green')))
fig_vol.update_layout(title=f"🔮 {TICKER} Volatility Forecast ({FORECAST_HORIZON}-Day Horizon)",
                      xaxis_title='Date', yaxis_title='Volatility (%)',
                      template='plotly_white', hovermode='x unified')
fig_vol.show()

# Interactive Table
forecast_table = go.Figure(data=[go.Table(
    header=dict(values=["📅 Date", "📈 Forecasted Volatility (%)"],
                fill_color='paleturquoise', align='center'),
    cells=dict(values=[
        forecast_df['Date'].dt.strftime('%Y-%m-%d'),
        forecast_df['Forecasted Volatility (%)'].round(4)
    ],
        fill_color='lavender', align='center'))
])
forecast_table.update_layout(title="📌 Forecasted Volatility Table")
forecast_table.show()

⚙️ Fitting AR(1)-GARCH(1,1) with Student's t-distribution...
✅ Model fitted.

                              AR - GARCH Model Results                              
Dep. Variable:                         NVDA   R-squared:                       0.005
Mean Model:                              AR   Adj. R-squared:                  0.004
Vol Model:                            GARCH   Log-Likelihood:               -3506.24
Distribution:      Standardized Student's t   AIC:                           7024.48
Method:                  Maximum Likelihood   BIC:                           7055.78
                                              No. Observations:                 1362
Date:                      Tue, Jun 10 2025   Df Residuals:                     1360
Time:                              16:54:39   Df Model:                            2
                                  Mean Model                                 
                 coef    std err          t      P>|t|       95.0% Conf. Int.
-


🧪 Ljung–Box Tests:
  Lag 10: p = 0.2765 (✅ no autocorrelation)
  Lag 20: p = 0.4972 (✅ no autocorrelation)
  Lag 30: p = 0.6587 (✅ no autocorrelation)

🔮 Forecasting 10-day ahead volatility...


## 📊 GARCH Family Model Comparison for NVDA Returns

This section compares multiple volatility models from the **ARCH/GARCH family** to determine the best-fitting model for **NVIDIA (NVDA)** log returns based on **Akaike Information Criterion (AIC)** and **Bayesian Information Criterion (BIC)**.

---

### ⚙️ Model Specifications:
The following models were fitted:

| Model Type                  | Distribution     |
|----------------------------|------------------|
| GARCH(1,1)                 | Normal / Student's t |
| EGARCH(1,1)                | Normal / Student's t |
| TARCH(1,1) Approximation   | Normal / Student's t |

---

### 📌 Evaluation Metrics:
- **AIC (Akaike Information Criterion):** Penalizes model complexity; lower is better.
- **BIC (Bayesian Information Criterion):** Stricter penalty on complexity; lower is better.

All models are estimated using `arch_model()` from the **`arch`** package.

---

### ✅ Process Summary:
1. Historical adjusted close prices were used to calculate **daily log returns**.
2. Six ARCH/GARCH-type models were estimated.
3. For each model, **AIC** and **BIC** scores were collected.
4. The **best model** was selected based on the **lowest AIC**.
5. The **conditional volatility series** of the best model was plotted interactively.

---

### 🏆 Best Model:
After evaluating all candidate models, the best-performing specification based on **lowest AIC** was:

```
[Model Name Inserted Programmatically]
```

This model provides the most parsimonious and best-fitting representation of NVDA's return volatility.

---

### 📈 Visualization:
- The interactive **Plotly chart** displays the **conditional volatility** over time.
- Hovering over the plot reveals exact dates and volatility values.
- Useful for **volatility regime analysis**, **risk management**, and **trading strategy calibration**.

---

In [84]:
# --- GARCH Family Model Comparison for NVDA Returns ---

# Data Preparation
TICKER = 'NVDA'
START_DATE = '2010-01-01'
END_DATE = '2025-06-06'

data = yf.download(TICKER, start=START_DATE, end=END_DATE, auto_adjust=True)
log_returns = 100 * np.log(data['Close'] / data['Close'].shift(1)).dropna()

# Define Model Specifications
print(f"\n--- Defining and Fitting Multiple ARCH/GARCH Models for {TICKER} ---")

models = {
    "GARCH(1,1) (Normal)": arch_model(log_returns, vol='Garch', p=1, q=1, dist="normal"),
    "EGARCH(1,1) (Normal)": arch_model(log_returns, vol='EGARCH', p=1, q=1, o=1, dist="normal"),
    "TARCH(1,1) Approx (Normal)": arch_model(log_returns, vol='Garch', p=1, q=1, power=1.0, dist="normal"),
    "GARCH(1,1) (StudentsT)": arch_model(log_returns, vol='Garch', p=1, q=1, dist="StudentsT"),
    "EGARCH(1,1) (StudentsT)": arch_model(log_returns, vol='EGARCH', p=1, q=1, o=1, dist="StudentsT"),
    "TARCH(1,1) Approx (StudentsT)": arch_model(log_returns, vol='Garch', p=1, q=1, power=1.0, dist="StudentsT")
}

results = {}
model_comparison_data = []

# Fit Each Model & Store Results
print("Fitting models...")
for name, mod in models.items():
    try:
        result = mod.fit(disp="off")
        results[name] = result
        model_comparison_data.append({
            'Model': name,
            'AIC': result.aic,
            'BIC': result.bic
        })
        print(f"✅ {name} fitted successfully.")
    except Exception as e:
        print(f"❌ Error fitting {name}: {e}")
        results[name] = None
        model_comparison_data.append({
            'Model': name,
            'AIC': np.nan,
            'BIC': np.nan
        })

# Tabular Comparison
model_comparison_df = pd.DataFrame(model_comparison_data)
model_comparison_df = model_comparison_df.sort_values(by='AIC').reset_index(drop=True)

print("\n--- Model Comparison Table (Sorted by AIC) ---")
print(model_comparison_df.to_string(index=False))

# Plot Conditional Volatility of Best Model
best_model_name = model_comparison_df.iloc[0]['Model']
best_result = results.get(best_model_name)

if best_result:
    print(f"\n🏆 Best Model Based on AIC: {best_model_name}")
    fig = go.Figure()

    fig.add_trace(go.Scattergl(
        x=best_result.conditional_volatility.index,
        y=best_result.conditional_volatility,
        name='Conditional Volatility',
        mode='lines',
        line=dict(color='indigo'),
        hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Volatility:</b> %{y:.4f}%<extra></extra>'
    ))

    fig.update_layout(
        title=f"{TICKER} - Conditional Volatility of Best GARCH-Type Model ({best_model_name})",
        xaxis_title='Date',
        yaxis_title='Conditional Volatility (%)',
        template='plotly_white',
        hovermode='x unified',
        margin=dict(l=20, r=20, t=60, b=20),
        legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1)
    )

    fig.show()
else:
    print(f"\n⚠️ Unable to display plot. Model fitting failed for: {best_model_name}")


[*********************100%***********************]  1 of 1 completed



--- Defining and Fitting Multiple ARCH/GARCH Models for NVDA ---
Fitting models...
✅ GARCH(1,1) (Normal) fitted successfully.
✅ EGARCH(1,1) (Normal) fitted successfully.
✅ TARCH(1,1) Approx (Normal) fitted successfully.
✅ GARCH(1,1) (StudentsT) fitted successfully.
✅ EGARCH(1,1) (StudentsT) fitted successfully.
✅ TARCH(1,1) Approx (StudentsT) fitted successfully.

--- Model Comparison Table (Sorted by AIC) ---
                        Model          AIC          BIC
      EGARCH(1,1) (StudentsT) 18037.084322 18074.664318
TARCH(1,1) Approx (StudentsT) 18064.562767 18095.879431
       GARCH(1,1) (StudentsT) 18101.675295 18132.991958
         EGARCH(1,1) (Normal) 18612.442226 18643.758889
   TARCH(1,1) Approx (Normal) 18631.399022 18656.452353
          GARCH(1,1) (Normal) 18709.737776 18734.791106

🏆 Best Model Based on AIC: EGARCH(1,1) (StudentsT)


## **Advanced Conditional Volatility Modeling with EGARCH(1,1)**

This section estimates the **EGARCH(1,1)** model with **Student's t-distribution** on the daily log returns of **NVIDIA (NVDA)** between **2010-01-01** and **2025-06-05**.

---

### **Why EGARCH(1,1)?**
- EGARCH (Exponential GARCH) captures **asymmetries** (leverage effects), where negative shocks impact volatility differently than positive ones.
- Unlike standard GARCH, it models **log-variance**, ensuring non-negativity of volatility without parameter restrictions.

---

### **Model Specifications:**
- **Model Type:** EGARCH(1,1)
- **Distribution:** Student's t (to capture heavy tails)
- **Estimation Tool:** `arch_model()` from the `arch` Python package

---

### **Process Summary:**
1. Historical daily log returns of NVDA were calculated from adjusted closing prices.
2. An **EGARCH(1,1)** model was fitted with an AR(0) mean structure.
3. Conditional volatility was extracted and visualized.
4. Summary statistics and diagnostics were printed.

---

In [85]:
# Advanced Conditional Volatility Modeling with EGARCH(1,1)
## Ticker: NVDA | Model: EGARCH(1,1) with Student's t-distribution

# EGARCH(1,1) Model Estimation
model = arch_model(log_returns, vol='EGARCH', p=1, o=1, q=1, dist='StudentsT')
result = model.fit(disp='off')

# Extract Conditional Volatility
cond_vol = result.conditional_volatility

# Interactive Volatility Plot (Plotly)
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=cond_vol.index,
    y=cond_vol,
    mode='lines',
    name='Estimated Conditional Volatility',
    line=dict(color='darkgreen', width=1.8),
    hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Volatility:</b> %{y:.4f}%<extra></extra>'
))

fig.update_layout(
    title=f"{TICKER} - EGARCH(1,1) Volatility Estimate (Student’s t)",
    xaxis_title='Date',
    yaxis_title='Conditional Volatility (%)',
    template='plotly_white',
    hovermode='x unified',
    height=600,
    width=1000,
    margin=dict(l=40, r=40, t=80, b=40),
    legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1)
)

fig.show()

# Summary Output
print("\n📄 EGARCH(1,1) Model Summary:")
print(result.summary())



📄 EGARCH(1,1) Model Summary:
                        Constant Mean - EGARCH Model Results                        
Dep. Variable:                         NVDA   R-squared:                       0.000
Mean Model:                   Constant Mean   Adj. R-squared:                  0.000
Vol Model:                           EGARCH   Log-Likelihood:               -9012.54
Distribution:      Standardized Student's t   AIC:                           18037.1
Method:                  Maximum Likelihood   BIC:                           18074.7
                                              No. Observations:                 3879
Date:                      Tue, Jun 10 2025   Df Residuals:                     3878
Time:                              16:54:49   Df Model:                            1
                                Mean Model                                
                 coef    std err          t      P>|t|    95.0% Conf. Int.
-------------------------------------------------------

# **Financial Risk Management: VaR and CVaR Calculation Functions**

This section focuses on **quantifying and managing financial risk** using advanced time series models and simulation techniques. Measuring risk accurately is essential for effective **portfolio optimization**, **regulatory compliance**, and **capital allocation**.

---

**Objectives of This Section**

- Evaluate market risk using **model-based** and **non-parametric** techniques  
- Estimate **Value-at-Risk (VaR)** and **Conditional VaR (CVaR)**  
- Visualize **risk dynamics** and **tail events** using simulation and empirical distributions  
- Assess risk under **normal** and **heavy-tailed** assumptions  

---

**Core Risk Metrics**

| Metric            | Description                                                                 |
|------------------|-----------------------------------------------------------------------------|
| **Value-at-Risk (VaR)**     | Maximum expected loss at a given confidence level (e.g., 95%, 99%) over a specific time horizon |
| **Conditional VaR (CVaR)**  | Expected loss given that the loss exceeds the VaR threshold (also known as Expected Shortfall) |
| **Volatility**              | Standard deviation of returns; a proxy for uncertainty and dispersion |
| **Skewness / Kurtosis**     | Measures of asymmetry and tail heaviness; important in stress testing |

---

**Tools and Methods**

- **Historical Simulation**
- **Parametric (Variance-Covariance) Approach**
- **Monte Carlo Simulation**
- **GARCH-type Volatility Forecasting**
- **Scenario and Stress Testing**

> *Model-based techniques (e.g., EGARCH) allow time-varying volatility estimates and capture fat tails via Student's t-distribution.*

---

**Practical Applications**

- **Risk budgeting** for multi-asset portfolios  
- **Capital adequacy assessments** under Basel III/IV  
- **Hedging strategy design**  
- **Liquidity and tail risk analysis**

---

## **Value at Risk (VaR) and Conditional Value at Risk (CVaR) Calculation Functions**

This section introduces robust and reusable Python functions to compute **Value at Risk (VaR)** and **Conditional Value at Risk (CVaR)** — two essential metrics in financial risk management. The implementations include both **analytical (parametric)** and **historical simulation** methods, applicable to **single asset** and **multi-asset portfolio** structures.

---

### **Function Overview**

| Function Name               | Scope         | Method                | Distribution Assumption |
|----------------------------|---------------|-----------------------|--------------------------|
| `calc_analytical_single`   | Single Asset  | Analytical (Closed-form) | Normal               |
| `calc_analytical_multiple` | Portfolio     | Analytical (Closed-form) | Normal               |
| `calc_historical_single`   | Single Asset  | Historical Simulation | None                  |
| `calc_historical_multiple` | Portfolio     | Historical Simulation | None                  |

---

### **Analytical Method (Parametric Approach)**

This method assumes returns follow a **normal distribution**. It estimates Value at Risk (VaR) and Conditional Value at Risk (CVaR) as:

#### **VaR Formula:**
$$
\text{VaR}_\alpha = z_\alpha \cdot \sigma - \mu
$$

#### **CVaR Formula:**
$$
\text{CVaR}_\alpha = \frac{\phi(z_\alpha)}{\alpha} \cdot \sigma - \mu
$$

Where:

- $z_\alpha$: $(1 - \alpha)$ quantile from the standard normal distribution  
- $\phi(z_\alpha)$: Probability density function value at $z_\alpha$  
- $\mu$: Mean of returns  
- $\sigma$: Standard deviation of returns  

---

### **Historical Simulation Method (Non-Parametric Approach)**

This method makes **no distributional assumptions**. It uses the empirical distribution of historical returns.

#### **VaR Formula:**
$$
\text{VaR}_\alpha = - \text{Quantile}_\alpha(R)
$$

#### **CVaR Formula:**
$$
\text{CVaR}_\alpha = - \mathbb{E} \left[ R \mid R < -\text{VaR}_\alpha \right]
$$

Where:

- $R$: Historical return vector  
- $\text{Quantile}_\alpha(R)$: Empirical quantile at level $\alpha$  

---

### **Data Validation Utilities**

- `check_returns_dataframe()`: Ensures return input is non-empty and numeric  
- `check_weights_vector()`: Validates weight vector shape matches returns  

These checks enhance **robustness** and reduce **debugging issues**.

---

### **Function Output Format**

Each function returns a tuple:
$$
(\text{VaR}_\alpha, \text{CVaR}_\alpha)
$$

Where $\alpha$ is the significance level (e.g., 0.05 for 95% confidence).

---

In [86]:
# Financial Risk Management: VaR and CVaR Calculation Functions

# Helper Functions: Data Validations
def check_returns_dataframe(ret: pd.DataFrame, func_name: str):
    if not isinstance(ret, pd.DataFrame) or ret.empty:
        raise ValueError(f"❌ {func_name}: 'ret' (returns) must be a valid and non-empty DataFrame.")
    if not pd.api.types.is_numeric_dtype(ret.iloc[:, 0]):
        warnings.warn(f"⚠️ {func_name}: Columns of the returns DataFrame are not numeric. Calculations may fail.")

def check_weights_vector(w: pd.DataFrame, ret: pd.DataFrame, func_name: str):
    if not isinstance(w, pd.DataFrame) or w.empty:
        raise ValueError(f"❌ {func_name}: 'w' (weights) must be a valid and non-empty DataFrame.")
    if w.shape[0] != ret.shape[1]:
        raise ValueError(f"❌ {func_name}: The weights DataFrame ({w.shape[0]} rows) must match the number of columns in the returns DataFrame ({ret.shape[1]}).")
    if not pd.api.types.is_numeric_dtype(w.iloc[:, 0]):
        warnings.warn(f"⚠️ {func_name}: The column of the weights DataFrame is not numeric. Calculations may fail.")

# Analytical VaR and CVaR
def calc_analytical_single(ret: pd.DataFrame, alpha: float) -> Tuple[float, float]:
    check_returns_dataframe(ret, "calc_analytical_single")
    if ret.shape[1] > 1:
        warnings.warn("⚠️ calc_analytical_single: Multiple columns provided. Only the first will be used.")
        ret = ret.iloc[:, [0]]
    z = norm.ppf(1 - alpha)
    var_calc = z * ret.std() - ret.mean()
    cvar_calc = (norm.pdf(norm.ppf(alpha)) / alpha) * ret.std() - ret.mean()
    return var_calc.iloc[0], cvar_calc.iloc[0]

def calc_analytical_multiple(ret: pd.DataFrame, w: pd.DataFrame, alpha: float) -> Tuple[float, float]:
    check_returns_dataframe(ret, "calc_analytical_multiple")
    check_weights_vector(w, ret, "calc_analytical_multiple")
    mu = ret.mean()
    Q = ret.cov()
    stdp = np.sqrt(w.T.dot(Q).dot(w)).iloc[0, 0]
    mup = mu.T.dot(w).iloc[0]
    z = norm.ppf(1 - alpha)
    var_calc = z * stdp - mup
    cvar_calc = (norm.pdf(norm.ppf(alpha)) / alpha) * stdp - mup
    return var_calc, cvar_calc

# Historical Simulation VaR and CVaR
def calc_historical_single(ret: pd.DataFrame, alpha: float) -> Tuple[float, float]:
    check_returns_dataframe(ret, "calc_historical_single")
    if ret.shape[1] > 1:
        warnings.warn("⚠️ calc_historical_single: Multiple columns provided. Only the first will be used.")
        ret = ret.iloc[:, [0]]
    var = -ret.quantile(q=alpha, interpolation='linear').iloc[0]
    cvar = -ret[ret.iloc[:, 0] < -var].mean().iloc[0]
    return var, cvar

def calc_historical_multiple(ret: pd.DataFrame, w: pd.DataFrame, alpha: float) -> Tuple[float, float]:
    check_returns_dataframe(ret, "calc_historical_multiple")
    check_weights_vector(w, ret, "calc_historical_multiple")
    weighted_ret = ret.dot(w).iloc[:, 0]
    var = -weighted_ret.quantile(q=alpha, interpolation='linear')
    cvar = -weighted_ret[weighted_ret < -var].mean()
    return var, cvar

# Monte Carlo Simulation Methods

def calc_mcs_multiple_normal(ret: pd.DataFrame, w: pd.DataFrame, alpha: float,
                             num_simulations: int = 100_000, random_state: int = None) -> Tuple[float, float]:
    """
    Monte Carlo Simulation - Multivariate Normal
    """
    check_returns_dataframe(ret, "calc_mcs_multiple_normal")
    check_weights_vector(w, ret, "calc_mcs_multiple_normal")
    np.random.seed(random_state)
    mu = ret.mean().values
    cov = ret.cov().values
    sims = np.random.multivariate_normal(mu, cov, size=num_simulations)
    port_sims = sims.dot(w.values)
    var = -np.quantile(port_sims, alpha)
    cvar = -port_sims[port_sims <= -var].mean()
    return var, cvar

def calc_mcs_multiple_t(ret: pd.DataFrame, w: pd.DataFrame, alpha: float,
                        df: int = 4, num_simulations: int = 100_000, random_state: int = None) -> Tuple[float, float]:
    """
    Monte Carlo Simulation - Student’s t Distribution
    """
    check_returns_dataframe(ret, "calc_mcs_multiple_t")
    check_weights_vector(w, ret, "calc_mcs_multiple_t")
    np.random.seed(random_state)
    mu = ret.mean().values
    cov = ret.cov().values
    d = np.random.chisquare(df, size=num_simulations) / df
    z = np.random.multivariate_normal(np.zeros(len(mu)), cov, size=num_simulations)
    sims = mu + z / np.sqrt(d)[:, None]
    port_sims = sims.dot(w.values)
    var = -np.quantile(port_sims, alpha)
    cvar = -port_sims[port_sims <= -var].mean()
    return var, cvar

print("✅ All VaR and CVaR calculation functions successfully loaded.")


✅ All VaR and CVaR calculation functions successfully loaded.


## **Financial Data Preparation and Portfolio Weighting**

This section handles the **acquisition and processing** of historical financial data, followed by the **portfolio construction based on user-defined quantities**.

---

### **Configuration Summary**

- **Tickers Selected**:  
  `MSFT`, `NVDA`, `INTC`, `AMD`, `ADBE`  
- **Date Range**:  
  From `2021-01-01` to `2025-06-06`
- **Interval**:  
  Daily closing prices (`1d`)
- **Confidence Level**:  
  $\alpha = 0.05$ (for 95% confidence)
- **Quantities Held**:  
  1 share per stock for simulation

---

### **Data Acquisition**

- Downloads adjusted daily closing prices using `yfinance`
- Cleans the data and removes rows with all missing values
- Displays first and last 5 observations for visual inspection

---

### **Return Calculation**

- Computes **daily simple returns** using:
  $$
  R_t = \frac{P_t - P_{t-1}}{P_{t-1}} = \frac{P_t}{P_{t-1}} - 1
  $$
- Drops rows with NaNs caused by differencing
- Displays a preview of the computed return matrix

---

### **Portfolio Valuation and Weighting**

1. **Latest Price Extraction**:  
   Selects the most recent non-null closing price for each asset

2. **Absolute Weights Calculation**:  
   Uses quantity × price per asset  
   $$
   u_i = q_i \cdot P_i
   $$

3. **Total Portfolio Value**:  
   $$
   W = \sum u_i
   $$

4. **Relative Weights**:  
   Computed as percentage contribution of each asset  
   $$
   w_i = \frac{u_i}{W}
   $$

5. **Formatted Tables**:
   - Absolute weights in USD
   - Relative weights as percentages

---

### **Output**

- Cleaned price matrix
- Return matrix
- Portfolio value ($W$)
- Absolute and relative weights ($u$, $w$)

This structured dataset is now ready for downstream **risk analysis, VaR/CVaR modeling, and portfolio simulation**.

---

In [87]:
# Financial Data Preparation and Portfolio Weights Calculation

print("🔄 Starting financial data download and portfolio preparation...")

# --- Configuration ---
TICKERS_TO_ANALYZE = ["MSFT", "NVDA", "INTC", "AMD", "ADBE"]
START_DATE = "2020-06-05"
END_DATE = "2025-06-06"
INTERVAL = "1d"
ALPHA = 0.05

QUANTITIES_HELD = pd.DataFrame(
    data=[1, 1, 1, 1, 1],
    index=TICKERS_TO_ANALYZE,
    columns=["quantity"]
)

print("\n📌 Configuration Summary:")
print(f"   - Tickers         : {TICKERS_TO_ANALYZE}")
print(f"   - Start Date      : {START_DATE}")
print(f"   - End Date        : {END_DATE}")
print(f"   - Data Interval   : {INTERVAL}")
print(f"   - Alpha (Risk Level): {ALPHA}")
print(f"   - Quantities Held:\n{QUANTITIES_HELD.to_string(index=True)}")

# --- Download Data ---
try:
    print(f"\n📥 Downloading data for {TICKERS_TO_ANALYZE}...")
    data = yf.download(
        tickers=TICKERS_TO_ANALYZE,
        start=START_DATE,
        end=END_DATE,
        interval=INTERVAL,
        auto_adjust=True,
        progress=False
    )

    if 'Close' in data.columns:
        prices = data['Close'].dropna(how='all')
        if prices.empty:
            raise ValueError("No valid 'Close' price found in downloaded data.")
        print("✅ Price data successfully downloaded and cleaned.")
        display(prices.head())
        display(prices.tail())

    elif len(TICKERS_TO_ANALYZE) == 1 and data.ndim == 2:
        prices = data['Close'].dropna()
        if prices.empty:
            raise ValueError(f"No valid 'Close' price found for {TICKERS_TO_ANALYZE[0]}.")
        print(f"✅ Price data for {TICKERS_TO_ANALYZE[0]} successfully downloaded and cleaned.")
        display(prices.head())
        display(prices.tail())
    else:
        raise ValueError("Unexpected data format. 'Close' column not found.")

except Exception as e:
    print(f"❌ Error during data download or processing: {e}")
    prices, returns, QUANTITIES_HELD = pd.DataFrame(), pd.DataFrame(), pd.DataFrame()
    W, u, w = np.nan, pd.DataFrame(), pd.DataFrame()
    raise

# --- Compute Returns ---
if not prices.empty:
    print("\n📊 Calculating daily returns...")
    returns = prices.pct_change().dropna(how='all')
    print("✅ Daily returns successfully calculated.")
    display(returns.head())
    display(returns.tail())
else:
    print("⚠️ Returns could not be calculated due to missing price data.")
    returns = pd.DataFrame()

# --- Portfolio Value and Weights ---
if not prices.empty and not QUANTITIES_HELD.empty:
    try:
        print("\n📦 Calculating portfolio value and weights...")
        latest_prices = prices.iloc[-1]
        u = QUANTITIES_HELD['quantity'] * latest_prices
        u = u.to_frame(name='absolute_weight')
        W = u['absolute_weight'].sum()
        w = u / W
        print("✅ Portfolio value and weights successfully calculated.")
        print(f'\n💰 Total Portfolio Value (W): ${W:,.2f}')
        print('\n💲 Absolute Weights (u - in $):')
        display(u.transpose().style.format({col: '${:,.2f}' for col in u.index}))
        print('\n⚖️ Relative Weights (w - %):')
        display(w.transpose().style.format({col: '{:.2%}' for col in w.index}))

    except Exception as e:
        print(f"❌ Error calculating portfolio value or weights: {e}")
        W, u, w = np.nan, pd.DataFrame(), pd.DataFrame()
else:
    print("⚠️ Portfolio value and weights could not be calculated due to missing data.")
    W, u, w = np.nan, pd.DataFrame(), pd.DataFrame()

print("\n🏁 Data preparation and portfolio weight calculation completed.")


🔄 Starting financial data download and portfolio preparation...

📌 Configuration Summary:
   - Tickers         : ['MSFT', 'NVDA', 'INTC', 'AMD', 'ADBE']
   - Start Date      : 2020-06-05
   - End Date        : 2025-06-06
   - Data Interval   : 1d
   - Alpha (Risk Level): 0.05
   - Quantities Held:
      quantity
MSFT         1
NVDA         1
INTC         1
AMD          1
ADBE         1

📥 Downloading data for ['MSFT', 'NVDA', 'INTC', 'AMD', 'ADBE']...
✅ Price data successfully downloaded and cleaned.


Ticker            ADBE        AMD       INTC        MSFT      NVDA
Date                                                              
2020-06-05  392.899994  53.099998  57.355453  179.353638  8.891313
2020-06-08  397.779999  52.970001  56.758183  180.465012  8.776684
2020-06-09  397.160004  56.389999  56.196579  181.844666  9.016908
2020-06-10  406.820007  57.439999  56.936470  188.589584  9.336625
2020-06-11  387.670013  52.830002  53.219151  178.462616  8.767960

Ticker            ADBE         AMD       INTC        MSFT        NVDA
Date                                                                 
2025-05-30  415.089996  110.730003  19.549999  460.359985  135.130005
2025-06-02  403.399994  114.629997  19.740000  461.970001  137.380005
2025-06-03  412.489990  117.309998  20.290001  462.970001  141.220001
2025-06-04  413.910004  118.580002  20.250000  463.869995  141.919998
2025-06-05  415.200012  115.690002  19.990000  467.679993  139.990005


📊 Calculating daily returns...
✅ Daily returns successfully calculated.


Ticker          ADBE       AMD      INTC      MSFT      NVDA
Date                                                        
2020-06-08  0.012420 -0.002448 -0.010413  0.006197 -0.012892
2020-06-09 -0.001559  0.064565 -0.009895  0.007645  0.027371
2020-06-10  0.024323  0.018620  0.013166  0.037092  0.035458
2020-06-11 -0.047072 -0.080258 -0.065289 -0.053698 -0.060907
2020-06-12  0.048675  0.012682 -0.006198  0.007892  0.015490

Ticker          ADBE       AMD      INTC      MSFT      NVDA
Date                                                        
2025-05-30  0.004185 -0.020349 -0.034568  0.003663 -0.029169
2025-06-02 -0.028163  0.035221  0.009719  0.003497  0.016651
2025-06-03  0.022533  0.023380  0.027862  0.002165  0.027952
2025-06-04  0.003443  0.010826 -0.001971  0.001944  0.004957
2025-06-05  0.003117 -0.024372 -0.012840  0.008214 -0.013599


📦 Calculating portfolio value and weights...
✅ Portfolio value and weights successfully calculated.

💰 Total Portfolio Value (W): $1,158.55

💲 Absolute Weights (u - in $):



⚖️ Relative Weights (w - %):



🏁 Data preparation and portfolio weight calculation completed.


## **Analytical Value at Risk (VaR) and Conditional Value at Risk (CVaR)**

This section computes **analytical VaR and CVaR** under the assumption of **normally distributed returns**. It includes both **relative (%)** and **absolute ($)** risk metrics using multiple approaches.

---

### **Confidence Level**

Let the confidence level be:

$$
\alpha = 0.05 \quad \text{(which corresponds to 95% confidence)}
$$

---

### **Relative VaR and CVaR (Percentage Terms)**

#### **Single Asset Approximation (Weighted Returns)**

Treat the portfolio as a single synthetic asset by computing:

$$
R_p = \sum_{i=1}^n w_i R_i
$$

Then, apply the analytical formulas assuming normality:

$$
\text{VaR}_\alpha = z_\alpha \cdot \sigma - \mu
$$

$$
\text{CVaR}_\alpha = \frac{\phi(z_\alpha)}{\alpha} \cdot \sigma - \mu
$$

**Where:**

$$
z_\alpha \quad \text{: Quantile from the standard normal distribution}
$$

$$
\phi(z_\alpha) \quad \text{: Probability density function (PDF) of the standard normal at } z_\alpha
$$

$$
\mu \quad \text{: Mean of returns}
$$

$$
\sigma \quad \text{: Standard deviation of returns}
$$

---

#### **Multi-Asset Approximation (Covariance-Based)**

Use the full return vector and weight vector:

$$
\sigma_p = \sqrt{w^\top \Sigma w}, \quad \mu_p = w^\top \mu
$$

Then compute:

$$
\text{VaR}_\alpha = z_\alpha \cdot \sigma_p - \mu_p
$$

$$
\text{CVaR}_\alpha = \frac{\phi(z_\alpha)}{\alpha} \cdot \sigma_p - \mu_p
$$

---

### **Absolute VaR and CVaR (in $USD)**

#### **Derived from Relative Measures**

Simply multiply the relative measures with the current portfolio value \( W \):

$$
\text{VaR}^{\$} = W \cdot \text{VaR}_\alpha
$$

$$
\text{CVaR}^{\$} = W \cdot \text{CVaR}_\alpha
$$

---

#### **Direct Portfolio Value Change Method**

Treat the absolute changes in portfolio value as a time series:

$$
\Delta V_t = \sum_{i=1}^n u_i \cdot R_{i,t}
$$

Apply the same single-asset VaR/CVaR formulas directly to \( \Delta V_t \).

---

In [88]:
# Analytical VaR and CVaR Calculations

print("🔄 Starting analytical VaR and CVaR calculations...")

# Confidence Level Definition
try:
    alpha = alpha
except NameError:
    print("⚠️ 'alpha' is not defined. Defaulting to 0.05.")
    alpha = 0.05

# Relative VaR and CVaR Calculations (in %)
print("\n📊 Relative VaR and CVaR Calculations (in %)")

# Approach 1: Single Asset Approximation (weighted portfolio return)
try:
    portfolio_returns_relative = returns.dot(w).iloc[:, 0]
    relative_var_single_asset, relative_cvar_single_asset = calc_analytical_single(
        portfolio_returns_relative.to_frame(name='PortfolioReturn'),
        alpha
    )
    print(f"  - Single Asset Approximation (Weighted Return): VaR = {relative_var_single_asset:.6f}, CVaR = {relative_cvar_single_asset:.6f}")
except Exception as e:
    print(f"  ❌ Error in Single Asset Approximation (Weighted Return): {e}")
    relative_var_single_asset, relative_cvar_single_asset = np.nan, np.nan

# Approach 2: Multi-Asset Approximation using covariance matrix
try:
    relative_var_multi_asset, relative_cvar_multi_asset = calc_analytical_multiple(
        returns,
        w,
        alpha
    )
    print(f"  - Multi-Asset Approximation (Covariance): VaR = {relative_var_multi_asset:.6f}, CVaR = {relative_cvar_multi_asset:.6f}")
except Exception as e:
    print(f"  ❌ Error in Multi-Asset Approximation (Covariance): {e}")
    relative_var_multi_asset, relative_cvar_multi_asset = np.nan, np.nan

# Absolute VaR and CVaR Calculations ($) using relative values
print("\n💵 Absolute VaR and CVaR Calculations (in $)")

try:
    current_portfolio_value = W
    if isinstance(current_portfolio_value, (pd.Series, np.ndarray)):
        current_portfolio_value = current_portfolio_value.item()
    elif not isinstance(current_portfolio_value, (int, float)):
        raise TypeError(f"W is not numeric. Type: {type(current_portfolio_value)}")

    if np.isnan(relative_var_multi_asset):
        print("  ⚠️ Relative VaR (Multi-Asset) is NaN. Cannot compute absolute VaR.")
        absolute_var_from_relative = np.nan
    else:
        absolute_var_from_relative = current_portfolio_value * relative_var_multi_asset

    if np.isnan(relative_cvar_multi_asset):
        print("  ⚠️ Relative CVaR (Multi-Asset) is NaN. Cannot compute absolute CVaR.")
        absolute_cvar_from_relative = np.nan
    else:
        absolute_cvar_from_relative = current_portfolio_value * relative_cvar_multi_asset

    print(f"  - Absolute VaR/CVaR Derived from Relative (Multi-Asset): VaR = ${absolute_var_from_relative:,.2f}, CVaR = ${absolute_cvar_from_relative:,.2f}")
except Exception as e:
    print(f"  ❌ Error in Absolute VaR/CVaR (Derived from Relative): {e}")
    absolute_var_from_relative, absolute_cvar_from_relative = np.nan, np.nan

# Absolute VaR and CVaR Based on Absolute Returns ($)
print("\n💵 Absolute VaR and CVaR Calculations (in $) - Based on Absolute Returns")

# Approach 3: Treat portfolio value change as a single asset
try:
    portfolio_absolute_change = returns.dot(u)
    absolute_var_direct_single, absolute_cvar_direct_single = calc_analytical_single(
        portfolio_absolute_change,
        alpha
    )
    print(f"  - Single Asset Approximation (Using Absolute Return): VaR = ${absolute_var_direct_single:,.2f}, CVaR = ${absolute_cvar_direct_single:,.2f}")
except Exception as e:
    print(f"  ❌ Error in Single Asset Approximation (Using Absolute Return): {e}")
    absolute_var_direct_single, absolute_cvar_direct_single = np.nan, np.nan

print("\n🏁 Analytical VaR and CVaR calculations completed.")


🔄 Starting analytical VaR and CVaR calculations...

📊 Relative VaR and CVaR Calculations (in %)
  - Single Asset Approximation (Weighted Return): VaR = 0.030600, CVaR = 0.038606
  - Multi-Asset Approximation (Covariance): VaR = 0.030600, CVaR = 0.038606

💵 Absolute VaR and CVaR Calculations (in $)
  - Absolute VaR/CVaR Derived from Relative (Multi-Asset): VaR = $35.45, CVaR = $44.73

💵 Absolute VaR and CVaR Calculations (in $) - Based on Absolute Returns
  - Single Asset Approximation (Using Absolute Return): VaR = $35.45, CVaR = $44.73

🏁 Analytical VaR and CVaR calculations completed.


## **Historical Simulation-Based VaR and CVaR Calculations**

This method estimates **Value at Risk (VaR)** and **Conditional Value at Risk (CVaR)** without assuming any specific distribution for asset returns. Instead, it utilizes the empirical distribution of historical returns.

---

### **Relative VaR and CVaR (in %)**

#### **Approach 1 – Single Asset Approximation  **
The portfolio is treated as a single synthetic asset using the weighted returns of individual assets:

$$
\text{Portfolio Return}_t = \sum_{i=1}^{N} w_i \cdot r_{i,t}
$$

- **VaR:**

$$
\text{VaR}_\alpha = -\text{Quantile}_\alpha(R)
$$

- **CVaR:**

$$
\text{CVaR}_\alpha = -\mathbb{E} \left[ R \mid R < -\text{VaR}_\alpha \right]
$$

Where:
- \( R \) is the empirical return distribution  
- \( \alpha \) is the significance level (e.g., 0.05 for 95% confidence)

---

#### **Approach 2 – Multi-Asset Approximation**
This method directly uses the historical returns matrix and the current portfolio weight vector:

- Portfolio return:

$$
R^{(p)}_t = \mathbf{w}^\top \cdot \mathbf{r}_t
$$

Then compute empirical quantiles and conditional expectations for VaR and CVaR as above.

---

### **Absolute VaR and CVaR (in \$)**

#### **From Relative VaR/CVaR:**

Absolute values are obtained by scaling relative values by the total portfolio value \( W \):

$$
\text{VaR}_{\text{abs}} = W \cdot \text{VaR}_{\text{rel}}
$$

$$
\text{CVaR}_{\text{abs}} = W \cdot \text{CVaR}_{\text{rel}}
$$

---

#### **Direct Dollar-Based Approach:**

Alternatively, use the dollar changes in portfolio value (i.e., \( \Delta P_t = \mathbf{r}_t^\top \cdot \mathbf{u} \)) directly:

- **VaR:**

$$
\text{VaR}_\alpha = -\text{Quantile}_\alpha(\Delta P)
$$

- **CVaR:**

$$
\text{CVaR}_\alpha = -\mathbb{E} \left[ \Delta P \mid \Delta P < -\text{VaR}_\alpha \right]
$$

---

### **Summary**

- The **historical simulation** method is **non-parametric** and **distribution-free**.
- Accurately captures **fat tails** and **skewness** in empirical returns.
- Both **relative (%)** and **absolute ($)** risk metrics provide complementary views.

---

In [89]:
# Historical Simulation Method for VaR and CVaR Calculations

print("🔄 Starting historical simulation-based VaR and CVaR calculations...")

# --- Relative VaR and CVaR Calculations (in %) ---
print("\n📊 Relative VaR and CVaR Calculations (in %)")

# Approach 1: Single Asset using weighted portfolio return
try:
    relative_var_hist_single_asset, relative_cvar_hist_single_asset = calc_historical_single(
        portfolio_returns_relative.to_frame(name='PortfolioReturn'),
        alpha
    )
    print(f"  - Single Asset Approach (Weighted Return): VaR = {relative_var_hist_single_asset:.6f}, CVaR = {relative_cvar_hist_single_asset:.6f}")
except Exception as e:
    print(f"  ❌ Error in Single Asset Approach (Weighted Return): {e}")
    relative_var_hist_single_asset, relative_cvar_hist_single_asset = np.nan, np.nan

# Approach 2: Multi-asset using returns + weights
try:
    relative_var_hist_multi_asset, relative_cvar_hist_multi_asset = calc_historical_multiple(
        returns,
        w,
        alpha
    )
    print(f"  - Multi-Asset Approach (Using returns + weights): VaR = {relative_var_hist_multi_asset:.6f}, CVaR = {relative_cvar_hist_multi_asset:.6f}")
except Exception as e:
    print(f"  ❌ Error in Multi-Asset Approach (Using returns + weights): {e}")
    relative_var_hist_multi_asset, relative_cvar_hist_multi_asset = np.nan, np.nan

# --- Absolute VaR and CVaR Calculations ($) using relative results ---
print("\n💵 Absolute VaR and CVaR Calculations (in $)")

try:
    current_portfolio_value = W
    if isinstance(current_portfolio_value, (pd.Series, np.ndarray)):
        current_portfolio_value = current_portfolio_value.item()
    elif not isinstance(current_portfolio_value, (int, float)):
        raise TypeError(f"'W' is not numeric. Type: {type(current_portfolio_value)}")

    if np.isnan(relative_var_hist_multi_asset):
        print("  ⚠️ Relative VaR (Historical Multi-Asset) is NaN. Cannot compute absolute VaR.")
        absolute_var_hist_from_relative = np.nan
    else:
        absolute_var_hist_from_relative = current_portfolio_value * relative_var_hist_multi_asset

    if np.isnan(relative_cvar_hist_multi_asset):
        print("  ⚠️ Relative CVaR (Historical Multi-Asset) is NaN. Cannot compute absolute CVaR.")
        absolute_cvar_hist_from_relative = np.nan
    else:
        absolute_cvar_hist_from_relative = current_portfolio_value * relative_cvar_hist_multi_asset

    print(f"  - Absolute VaR/CVaR Derived from Relative (Historical Multi-Asset): VaR = ${absolute_var_hist_from_relative:,.2f}, CVaR = ${absolute_cvar_hist_from_relative:,.2f}")

except Exception as e:
    print(f"  ❌ Error in Absolute VaR/CVaR (Derived from Relative - Historical): {e}")
    absolute_var_hist_from_relative, absolute_cvar_hist_from_relative = np.nan, np.nan

# --- Absolute VaR and CVaR Based on Dollar Portfolio Change ---
print("\n💵 Absolute VaR and CVaR Calculations (in $) - Based on Absolute Returns")

# Approach 3: Use daily absolute portfolio value changes
try:
    absolute_var_hist_direct_single, absolute_cvar_hist_direct_single = calc_historical_single(
        portfolio_absolute_change,
        alpha
    )
    print(f"  - Single Asset Approach (Using Absolute Return - Historical): VaR = ${absolute_var_hist_direct_single:,.2f}, CVaR = ${absolute_cvar_hist_direct_single:,.2f}")
except Exception as e:
    print(f"  ❌ Error in Single Asset Approach (Using Absolute Return - Historical): {e}")
    absolute_var_hist_direct_single, absolute_cvar_hist_direct_single = np.nan, np.nan

print("\n🏁 Historical simulation VaR and CVaR calculations completed.")


🔄 Starting historical simulation-based VaR and CVaR calculations...

📊 Relative VaR and CVaR Calculations (in %)
  - Single Asset Approach (Weighted Return): VaR = 0.033176, CVaR = 0.043517
  - Multi-Asset Approach (Using returns + weights): VaR = 0.033176, CVaR = 0.043517

💵 Absolute VaR and CVaR Calculations (in $)
  - Absolute VaR/CVaR Derived from Relative (Historical Multi-Asset): VaR = $38.44, CVaR = $50.42

💵 Absolute VaR and CVaR Calculations (in $) - Based on Absolute Returns
  - Single Asset Approach (Using Absolute Return - Historical): VaR = $38.44, CVaR = $50.42

🏁 Historical simulation VaR and CVaR calculations completed.


## **Monte Carlo Simulation for VaR/CVaR and Kupiec Test**

This section performs advanced Value-at-Risk (VaR) and Conditional Value-at-Risk (CVaR) analysis using **Monte Carlo simulations** under two distributional assumptions:  

- **Multivariate Normal distribution**
- **Multivariate Student's t-distribution** (with varying degrees of freedom)

We also evaluate the statistical validity of our risk model using the **Kupiec Unconditional Coverage Test**.

---

In [90]:
# Monte Carlo Simulation for VaR/CVaR and Kupiec Test

print("🔄 Preparing Monte Carlo simulation for VaR/CVaR and Kupiec Test...")

# Monte Carlo Simulation: Relative VaR and CVaR (Normal)
print("\n📊 Monte Carlo Simulation - Relative VaR and CVaR (Assuming Multivariate Normal Distribution)")

try:
    relative_var_mc_normal, relative_cvar_mc_normal = calc_mcs_multiple_normal(
        returns,
        w,
        alpha,
        num_simulations=1_000_000,
        random_state=100
    )
    print(f"  - MC (Normal): VaR = {relative_var_mc_normal:.6f}, CVaR = {relative_cvar_mc_normal:.6f}")
except Exception as e:
    print(f"  ❌ Error in MC (Normal): {e}")
    relative_var_mc_normal, relative_cvar_mc_normal = np.nan, np.nan

# Monte Carlo Simulation: Relative VaR and CVaR (Student’s t)
print("\n📊 Monte Carlo Simulation - Relative VaR and CVaR (Student’s t Distribution)")

degrees_of_freedom_list: List[int] = [4, 40, 400]

for df_value in degrees_of_freedom_list:
    try:
        relative_var_mc_t, relative_cvar_mc_t = calc_mcs_multiple_t(
            returns,
            w,
            alpha,
            df=df_value,
            num_simulations=1_000_000,
            random_state=100
        )
        print(f"  - MC (Student t, df={df_value}): VaR = {relative_var_mc_t:.6f}, CVaR = {relative_cvar_mc_t:.6f}")
    except Exception as e:
        print(f"  ❌ Error in MC (Student t, df={df_value}): {e}")
        continue

# --- Absolute VaR and CVaR Based on Relative MC (in $) ---
print("\n💵 Monte Carlo Simulation - Absolute VaR and CVaR (in $)")

try:
    current_portfolio_value = W
    if isinstance(current_portfolio_value, (pd.Series, np.ndarray)):
        current_portfolio_value = current_portfolio_value.item()
    elif not isinstance(current_portfolio_value, (int, float)):
        raise TypeError(f"'W' is not numeric. Type: {type(current_portfolio_value)}")

    if np.isnan(relative_var_mc_normal):
        print("  ⚠️ Relative VaR (MC Normal) is NaN. Absolute VaR cannot be calculated.")
        absolute_var_mc_from_relative = np.nan
    else:
        absolute_var_mc_from_relative = current_portfolio_value * relative_var_mc_normal

    if np.isnan(relative_cvar_mc_normal):
        print("  ⚠️ Relative CVaR (MC Normal) is NaN. Absolute CVaR cannot be calculated.")
        absolute_cvar_mc_from_relative = np.nan
    else:
        absolute_cvar_mc_from_relative = current_portfolio_value * relative_cvar_mc_normal

    print(f"  - Absolute VaR/CVaR from Relative (MC Normal): VaR = ${absolute_var_mc_from_relative:,.2f}, CVaR = ${absolute_cvar_mc_from_relative:,.2f}")

except Exception as e:
    print(f"  ❌ Error in Absolute VaR/CVaR (from Relative - MC Normal): {e}")
    absolute_var_mc_from_relative, absolute_cvar_mc_from_relative = np.nan, np.nan

# --- Direct Absolute VaR/CVaR using Absolute Portfolio Return (Monte Carlo) ---
print("\n💵 Monte Carlo Simulation - Absolute VaR and CVaR (Direct from Absolute Portfolio Change)")

try:
    portfolio_absolute_change = returns.dot(u)

    if isinstance(portfolio_absolute_change, pd.Series):
        portfolio_absolute_change_df = portfolio_absolute_change.to_frame(name='P_change')
    else:
        portfolio_absolute_change_df = portfolio_absolute_change.copy()
        portfolio_absolute_change_df.columns = ['P_change']

    weight_df = pd.DataFrame([1], index=['P_change'])

    absolute_var_mc_direct_single, absolute_cvar_mc_direct_single = calc_mcs_multiple_normal(
        portfolio_absolute_change_df,
        weight_df,
        alpha,
        num_simulations=1_000_000,
        random_state=100
    )

    print(f"  - Single Asset (Using Absolute Change - MC Normal): VaR = ${absolute_var_mc_direct_single:,.2f}, CVaR = ${absolute_cvar_mc_direct_single:,.2f}")

except Exception as e:
    print(f"  ❌ Error in Single Asset (Using Absolute Change - MC Normal): {e}")
    absolute_var_mc_direct_single, absolute_cvar_mc_direct_single = np.nan, np.nan

# --- Kupiec Unconditional Coverage Test ---
def perform_kupiec_test(actual_losses: pd.Series, var_values: pd.Series, p_expected: float) -> Tuple[float, int, int, float]:
    if not isinstance(actual_losses, pd.Series) or actual_losses.empty:
        raise ValueError("❌ 'actual_losses' must be a valid non-empty Series.")

    violations = actual_losses > var_values
    n = len(actual_losses)
    n1 = int(violations.sum())
    n0 = n - n1
    p_observed = n1 / n

    log_expected = (n0 * np.log(1 - p_expected) if n0 > 0 else 0) + \
                   (n1 * np.log(p_expected) if n1 > 0 else 0)
    log_observed = (n0 * np.log(1 - p_observed) if n0 > 0 else 0) + \
                   (n1 * np.log(p_observed) if n1 > 0 else 0)

    kupiec_stat = -2 * (log_expected - log_observed)
    pvalue = 1 - chi2.cdf(kupiec_stat, df=1)

    return kupiec_stat, n, n1, pvalue

# --- Example Application of Kupiec Test ---
print("\n🧪 Running Kupiec Unconditional Coverage Test")

try:
    actual_portfolio_losses_relative = -portfolio_returns_relative
    var_value_to_test = relative_var_hist_single_asset

    if not np.isnan(var_value_to_test):
        var_series_for_test = pd.Series(var_value_to_test, index=actual_portfolio_losses_relative.index)

        kupiec_stat, n_obs, n_violations, pvalue = perform_kupiec_test(
            actual_losses=actual_portfolio_losses_relative,
            var_values=var_series_for_test,
            p_expected=alpha
        )

        print(f"  - Tested VaR Value (e.g. Historical Simulation): {var_value_to_test:.6f}")
        print(f"  - Expected Violation Rate (alpha): {alpha:.2%}")
        print(f"  - Number of Observations: {n_obs}")
        print(f"  - Number of Violations: {n_violations}")
        print(f"  - Observed Violation Rate: {n_violations / n_obs:.2%}")
        print(f"  - Kupiec Test Statistic: {kupiec_stat:.4f}")
        print(f"  - p-value: {pvalue:.4f}")

        if pvalue < alpha:
            print(f"  - Conclusion: p-value ({pvalue:.4f}) < alpha ({alpha:.2%}) → Statistically INVALID model (H0 rejected).")
        else:
            print(f"  - Conclusion: p-value ({pvalue:.4f}) ≥ alpha ({alpha:.2%}) → Statistically VALID model (H0 not rejected).")
    else:
        print("  ⚠️ VaR value is NaN. Kupiec test cannot be performed.")

except Exception as e:
    print(f"❌ Error while applying Kupiec Test: {e}")

print("\n🏁 Monte Carlo simulation VaR/CVaR and Kupiec Test completed.")


🔄 Preparing Monte Carlo simulation for VaR/CVaR and Kupiec Test...

📊 Monte Carlo Simulation - Relative VaR and CVaR (Assuming Multivariate Normal Distribution)
  - MC (Normal): VaR = 0.030621, CVaR = 0.038623

📊 Monte Carlo Simulation - Relative VaR and CVaR (Student’s t Distribution)
  - MC (Student t, df=4): VaR = 0.039858, CVaR = 0.060417
  - MC (Student t, df=40): VaR = 0.031325, CVaR = 0.040103
  - MC (Student t, df=400): VaR = 0.030663, CVaR = 0.038739

💵 Monte Carlo Simulation - Absolute VaR and CVaR (in $)
  - Absolute VaR/CVaR from Relative (MC Normal): VaR = $35.48, CVaR = $44.75

💵 Monte Carlo Simulation - Absolute VaR and CVaR (Direct from Absolute Portfolio Change)
  - Single Asset (Using Absolute Change - MC Normal): VaR = $35.39, CVaR = $44.62

🧪 Running Kupiec Unconditional Coverage Test
  - Tested VaR Value (e.g. Historical Simulation): 0.033176
  - Expected Violation Rate (alpha): 5.00%
  - Number of Observations: 1256
  - Number of Violations: 63
  - Observed Violat

## **Backtesting of VaR Models-**

This section performs **rolling window backtesting** of various Value-at-Risk (VaR) models using historical financial return data. The objective is to validate the models by comparing **forecasted VaR values** with **actual portfolio losses**, and evaluate their accuracy using the **Kupiec Unconditional Coverage Test**.

---

### **Configuration**

- **In-sample window size (m):** 250 trading days  
- **Backtesting period (n):** Remaining observations  
- **Confidence levels (alphas):**  
  \[
  \{0.001, 0.005, 0.01, 0.05, 0.10, 0.15\}
  \]
- **Monte Carlo simulation parameters:**
  - Distribution: Student’s t  
  - Degrees of freedom: \( df = 4 \)  
  - Simulations: 1,000,000

---

### **VaR Models Evaluated**

1. **Parametric (Analytical VaR):**  
   Assumes normally distributed returns and uses analytical formulas.

2. **Historical Simulation:**  
   Uses empirical quantiles from past returns (non-parametric).

3. **Monte Carlo Simulation (Student's t, df=4):**  
   Generates returns via fat-tailed distribution and estimates VaR from simulated distribution.

---

### **Rolling Window Backtest Logic**

For each alpha level:

- Slide a window of length \( m = 250 \) across the time series.
- At each step:
  - Estimate each model’s VaR based on the in-sample data.
  - Compare to the **actual out-of-sample portfolio loss**.
  - Record whether a **violation** occurred (actual loss > VaR).

---

### **Backtesting Metrics Collected**

- **VaR Time Series:** For each alpha and model
- **True Losses:** Actual observed portfolio losses
- **Violations:** Number of exceedances over VaR
- **Kupiec Test p-values:** Validity of each model based on observed vs. expected violations

---

### **VaR Curves & Loss Visualization**

For each \( \alpha \), the following are plotted:

- True Losses (dots)
- Forecasted VaRs by each model (colored lines):
  - Red: Analytical
  - Blue: Historical
  - Green: Monte Carlo (t)

---

## **Example Output: Number of Violations (Exceptions)**

| Model               | α = 0.01 | α = 0.05 | ... |
|--------------------|----------|----------|-----|
| Analytical VaR     |   3      |   12     | ... |
| Historical VaR     |   4      |   15     | ... |
| Monte Carlo (t=4)  |   2      |   13     | ... |
| **Expected**       |   2.5    |   12.5   | ... |

---

### **Kupiec Unconditional Coverage Test**

For each alpha and model, the following is computed:

- **Number of Violations**
- **Observed Violation Rate** vs. Expected \( \alpha \)
- **Kupiec LR statistic**
- **p-value**: Statistical test of model accuracy

If $( \text{p-value} \geq \alpha)$: model is statistically **valid**  
If $( \text{p-value} < \alpha)$: model is **rejected**

---

### **Summary**

This backtest process enables:

- Comparative performance evaluation of VaR models  
- Visual inspection of forecast reliability  
- Statistical validation using Kupiec Test  

The models that strike a **balance between accuracy and conservative risk estimation** (i.e., p-value ≥ 0.05 and violations ≈ expected) are considered **statistically valid** under backtesting.

---

In [92]:
# Backtesting of VaR Models

# Required variables (returns, w) are assumed to be defined in previous cells.
# Required functions (calc_analytical_multiple, calc_historical_multiple,
# calc_mcs_multiple_t, perform_kupiec_test) are assumed to be defined as well.

warnings.filterwarnings('ignore', category=RuntimeWarning)

print("🔄 Starting backtesting of VaR models...")

# --- Configuration ---
ALPHAS_TO_TEST: List[float] = [0.001, 0.005, 0.01, 0.05, 0.10, 0.15]
IN_SAMPLE_LENGTH = 250
MC_STUDENT_T_DF = 4
MC_SIMULATIONS_COUNT = 1_000_000

if returns.empty:
    raise ValueError("❌ 'returns' DataFrame is empty.")
if w.empty:
    raise ValueError("❌ 'w' DataFrame (relative weights) is empty.")

total_data_points = len(returns)
BACKTEST_LENGTH = total_data_points - IN_SAMPLE_LENGTH

if BACKTEST_LENGTH <= 0:
    raise ValueError(f"❌ Backtest period is invalid. Total data ({total_data_points}) <= in-sample ({IN_SAMPLE_LENGTH}).")
if BACKTEST_LENGTH < max(1 / np.array(ALPHAS_TO_TEST)):
    warnings.warn(f"⚠️ Backtest period ({BACKTEST_LENGTH}) may be too short for smallest alpha ({min(ALPHAS_TO_TEST):.3f}).")

print("\n📌 Backtest Configuration:")
print(f"   - Total Data Points: {total_data_points}")
print(f"   - In-Sample Length (m): {IN_SAMPLE_LENGTH}")
print(f"   - Backtesting Length (n): {BACKTEST_LENGTH}")
print(f"   - Alphas to Test: {ALPHAS_TO_TEST}")
print(f"   - MC Student t df: {MC_STUDENT_T_DF}")

exceptions_df = pd.DataFrame(np.nan, columns=ALPHAS_TO_TEST, index=['Analytical', 'Historical', 'Monte Carlo (t=4)', 'Expected'])
pvalue_kupiec_df = pd.DataFrame(np.nan, columns=ALPHAS_TO_TEST, index=['Analytical', 'Historical', 'Monte Carlo (t=4)'])
VaRs_data_for_plotting = {}

print("\n⏳ Running rolling window backtesting...")

for i, alpha in enumerate(ALPHAS_TO_TEST):
    print(f"\n--- Testing for alpha = {alpha:.3f} ---")

    VaRs_for_alpha = pd.DataFrame(np.nan, index=returns.index[IN_SAMPLE_LENGTH:], columns=['Analytical', 'Historical', 'Monte Carlo (t=4)', 'True Loss'])

    for t in range(IN_SAMPLE_LENGTH, total_data_points):
        in_sample_returns = returns.iloc[t-IN_SAMPLE_LENGTH:t]
        out_of_sample_returns_row = returns.iloc[[t]]
        true_loss_relative = -out_of_sample_returns_row.dot(w).iloc[0, 0]

        try:
            var_analytical, _ = calc_analytical_multiple(in_sample_returns, w, alpha)
            VaRs_for_alpha.loc[returns.index[t], 'Analytical'] = var_analytical
        except: VaRs_for_alpha.loc[returns.index[t], 'Analytical'] = np.nan

        try:
            var_historical, _ = calc_historical_multiple(in_sample_returns, w, alpha)
            VaRs_for_alpha.loc[returns.index[t], 'Historical'] = var_historical
        except: VaRs_for_alpha.loc[returns.index[t], 'Historical'] = np.nan

        try:
            var_mc_t, _ = calc_mcs_multiple_t(in_sample_returns, w, alpha, df=MC_STUDENT_T_DF)
            VaRs_for_alpha.loc[returns.index[t], 'Monte Carlo (t=4)'] = var_mc_t
        except: VaRs_for_alpha.loc[returns.index[t], 'Monte Carlo (t=4)'] = np.nan

        VaRs_for_alpha.loc[returns.index[t], 'True Loss'] = true_loss_relative

        if (t - IN_SAMPLE_LENGTH + 1) % (BACKTEST_LENGTH // 10 or 1) == 0 or t == total_data_points - 1:
            print(f"    Step {t - IN_SAMPLE_LENGTH + 1}/{BACKTEST_LENGTH} complete ({(t - IN_SAMPLE_LENGTH + 1)/BACKTEST_LENGTH:.0%})")

    VaRs_data_for_plotting[alpha] = VaRs_for_alpha.copy()

    print(f"\n--- Violations and Kupiec Test for alpha = {alpha:.3f} ---")
    VaRs_valid = VaRs_for_alpha.dropna(subset=['True Loss'])

    if VaRs_valid.empty:
        print(f"  ⚠️ No valid VaR or True Loss for alpha = {alpha:.3f}.")
        continue

    for column in ['Analytical', 'Historical', 'Monte Carlo (t=4)']:
        if column in VaRs_valid.columns and not VaRs_valid[column].isnull().all():
            try:
                violations_series = VaRs_valid['True Loss'] > VaRs_valid[column]
                num_violations = int(violations_series.sum())
                exceptions_df.loc[column, alpha] = num_violations

                _, n_obs, _, pvalue = perform_kupiec_test(
                    actual_losses=VaRs_valid['True Loss'],
                    var_values=VaRs_valid[column],
                    p_expected=alpha
                )
                pvalue_kupiec_df.loc[column, alpha] = pvalue

                print(f"  - {column}: Violations = {num_violations}/{n_obs} ({num_violations/n_obs:.2%}), p-value = {pvalue:.4f}")
            except Exception as e:
                print(f"  ❌ Error ({column}, alpha={alpha:.3f}): {e}")
                exceptions_df.loc[column, alpha] = np.nan
                pvalue_kupiec_df.loc[column, alpha] = np.nan

    exceptions_df.loc['Expected', alpha] = alpha * BACKTEST_LENGTH

print("\n\n=== Backtesting Results ===")
print("\n📈 Number of VaR Violations:")
display(exceptions_df.style.format({a: '{:.0f}' for a in ALPHAS_TO_TEST}).background_gradient(cmap='Reds'))

print("\n📊 Kupiec Test p-values:")
def color_pvalue(val):
    if pd.isna(val): return ''
    return 'color: red' if val < 0.05 else 'color: green'

display(pvalue_kupiec_df.style.applymap(color_pvalue).format({a: '{:.4f}' for a in ALPHAS_TO_TEST}))

print("\n📉 VaR Curves and True Loss (Backtesting Period)")
# INTERACTIVE PLOTTING OF VAR BACKTESTING RESULTS

def plot_var_dropdown(VaRs_data_for_plotting, ALPHAS_TO_TEST):
    fig = go.Figure()
    color_map = {
        "True Loss": "gray",
        "Analytical": "red",
        "Historical": "blue",
        "Monte Carlo (t=4)": "green"
    }

    buttons = []
    for i, alpha in enumerate(ALPHAS_TO_TEST):
        df = VaRs_data_for_plotting.get(alpha)
        if df is None or df.empty:
            continue
        for model in ["True Loss", "Analytical", "Historical", "Monte Carlo (t=4)"]:
            fig.add_trace(go.Scatter(
                x=df.index,
                y=df[model],
                mode='lines+markers' if model == "True Loss" else 'lines',
                name=f"{model} (α={alpha})",
                visible=(i == 0),
                line=dict(color=color_map.get(model, 'black')),
                hovertemplate=f"<b>{model}</b><br>Date: %{{x|%Y-%m-%d}}<br>Value: %{{y:.4f}}<extra></extra>"
            ))

    total_traces = len(ALPHAS_TO_TEST) * 4
    for i, alpha in enumerate(ALPHAS_TO_TEST):
        visibility = [False] * total_traces
        for j in range(4):
            visibility[i * 4 + j] = True
        buttons.append(dict(
            label=f"α = {alpha:.3f}",
            method="update",
            args=[{"visible": visibility},
                  {"title": f"📉 VaR Backtesting Results (α = {alpha:.3f})"}]
        ))

    fig.update_layout(
        updatemenus=[{
            "buttons": buttons,
            "direction": "down",
            "showactive": True,
            "x": 0.85,
            "xanchor": "left",
            "y": 0.98,
            "yanchor": "top"
        }],
        title=f"📉 VaR Backtesting Results (α = {ALPHAS_TO_TEST[0]:.3f})",
        xaxis_title="Date",
        yaxis_title="VaRs & True Loss",
        template="plotly_white",
        height=600,
        width=1000,
        hovermode="x unified",
        margin=dict(l=60, r=40, t=60, b=40)
    )
    fig.show()

print("\n🏁 Backtesting process completed.")

plot_var_dropdown(VaRs_data_for_plotting, ALPHAS_TO_TEST)


🔄 Starting backtesting of VaR models...

📌 Backtest Configuration:
   - Total Data Points: 1256
   - In-Sample Length (m): 250
   - Backtesting Length (n): 1006
   - Alphas to Test: [0.001, 0.005, 0.01, 0.05, 0.1, 0.15]
   - MC Student t df: 4

⏳ Running rolling window backtesting...

--- Testing for alpha = 0.001 ---
    Step 100/1006 complete (10%)
    Step 200/1006 complete (20%)
    Step 300/1006 complete (30%)
    Step 400/1006 complete (40%)
    Step 500/1006 complete (50%)
    Step 600/1006 complete (60%)
    Step 700/1006 complete (70%)
    Step 800/1006 complete (80%)
    Step 900/1006 complete (89%)
    Step 1000/1006 complete (99%)
    Step 1006/1006 complete (100%)

--- Violations and Kupiec Test for alpha = 0.001 ---
  - Analytical: Violations = 7/1006 (0.70%), p-value = 0.0001
  - Historical: Violations = 6/1006 (0.60%), p-value = 0.0007
  - Monte Carlo (t=4): Violations = 0/1006 (0.00%), p-value = 0.1560

--- Testing for alpha = 0.005 ---
    Step 100/1006 complete (10%)


📊 Kupiec Test p-values:



📉 VaR Curves and True Loss (Backtesting Period)

🏁 Backtesting process completed.


# **Technical Analysis**

This analysis applies multiple technical indicators and trading signals to the stock **NVDA** using daily price data from **2024-01-01 to 2025-06-06**. It employs Plotly for dynamic visualizations and `ta` for technical indicators.

---

### **Data Configuration**

- **Ticker:** NVDA  
- **Date Range:** 2024-01-01 to 2025-06-06  
- **Interval:** Daily (`1d`)

---

### **Technical Indicators Applied**

# **Advanced Multi-Indicator Technical Analysis of NVIDIA (NVDA)**

This module performs a comprehensive technical analysis on NVIDIA Corporation (NVDA) stock using a wide range of popular indicators and visualization tools. The objective is to identify trend-following, momentum, volatility, and reversal signals in an integrated multi-chart layout.

### **Dataset Description**
- **Ticker:** NVDA (NVIDIA Corporation)
- **Data Source:** Yahoo Finance (`yfinance`)
- **Time Frame:** Daily data from `2024-01-01` to `2025-06-06`

### **Calculated Indicators**
- **Trend Indicators:**
  - Moving Averages: MA20, MA50, MA200
  - Exponential MAs: EMA12, EMA26
  - Ichimoku Cloud (Lines A & B)
- **Volatility Measures:**
  - Bollinger Bands (20-day)
  - Average True Range (ATR, 14-day)
- **Momentum Oscillators:**
  - Relative Strength Index (RSI, 14-day)
  - Moving Average Convergence Divergence (MACD & Signal Line)
  - Stochastic Oscillator (%K, %D)
  - Average Directional Index (ADX)
- **Support & Resistance:**
  - 20-day rolling minimum (Support)
  - 20-day rolling maximum (Resistance)
- **Fibonacci Retracement Levels:**
  - Derived from recent 100-day High-Low range

### **Signal Detection Logic**
- **Buy Signal:** When `MA20` crosses above `MA50`
- **Sell Signal:** When `MA20` crosses below `MA50`

### **Visualization Layout**
The analysis is visualized using a five-row multi-subplot Plotly chart:
1. **Price Chart** with Moving Averages, Bollinger Bands, Ichimoku Cloud, and Buy/Sell signals
2. **Volume** overlay
3. **MACD & Signal Line**
4. **RSI & ADX** with overbought/oversold thresholds
5. **Stochastic Oscillator** + Support/Resistance levels

This multi-layered approach aids in identifying trend continuations, potential reversals, and overall market sentiment for NVDA stock within the selected time frame.


In [93]:
# Configuration
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'

# Download Data
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=False).dropna()

# Flatten MultiIndex columns if any
if isinstance(data.columns, pd.MultiIndex):
    data.columns = [col[0] if isinstance(col, tuple) else col for col in data.columns]

# Series
high = data['High']
low = data['Low']
close = data['Close']

# Indicators
data['MA20'] = close.rolling(20).mean()
data['MA50'] = close.rolling(50).mean()
data['MA200'] = data['Adj Close'].rolling(200).mean()

bb = ta.volatility.BollingerBands(close=close, window=20)
data['BB_High'] = bb.bollinger_hband()
data['BB_Low'] = bb.bollinger_lband()
data['BB_Middle'] = bb.bollinger_mavg()

data['EMA12'] = close.ewm(span=12).mean()
data['EMA26'] = close.ewm(span=26).mean()
data['MACD'] = data['EMA12'] - data['EMA26']
data['MACD_Signal'] = data['MACD'].ewm(span=9).mean()

delta = close.diff()
gain = delta.where(delta > 0, 0).rolling(14).mean()
loss = -delta.where(delta < 0, 0).rolling(14).mean()
rs = gain / loss
data['RSI'] = 100 - (100 / (1 + rs))

data['ATR'] = ta.volatility.AverageTrueRange(high, low, close, window=14).average_true_range()
data['Support'] = low.rolling(20).min()
data['Resistance'] = high.rolling(20).max()

data['Signal_Position'] = np.where(data['MA20'] > data['MA50'], 1, np.where(data['MA20'] < data['MA50'], -1, 0))
data['Buy_Signal'] = (data['Signal_Position'] > data['Signal_Position'].shift(1)) & (data['Signal_Position'] == 1)
data['Sell_Signal'] = (data['Signal_Position'] < data['Signal_Position'].shift(1)) & (data['Signal_Position'] == -1)

# Ichimoku, ADX, Stochastic
ichimoku = IchimokuIndicator(high, low, window1=9, window2=26, window3=52)
data['Ichimoku_A'] = ichimoku.ichimoku_a()
data['Ichimoku_B'] = ichimoku.ichimoku_b()

data['ADX'] = ADXIndicator(high, low, close, window=14).adx()
stoch = StochasticOscillator(high, low, close, window=14)
data['Stoch_%K'] = stoch.stoch()
data['Stoch_%D'] = stoch.stoch_signal()

# Fibonacci
max_price = data['High'].iloc[-100:].max()
min_price = data['Low'].iloc[-100:].min()
fibo_levels = [0.0, 0.236, 0.382, 0.5, 0.618, 0.786, 1.0]
fibo_lines = {f"{int(level*100)}%": max_price - (max_price - min_price) * level for level in fibo_levels}

# Plot
fig = make_subplots(
    rows=5, cols=1, shared_xaxes=True, vertical_spacing=0.03,
    row_heights=[0.4, 0.1, 0.15, 0.15, 0.2],
    subplot_titles=[
        f"{ticker} Price with Indicators", "Volume", "MACD", "RSI + ADX", "Stochastic + Support/Resistance"
    ]
)

# Row 1 - Price & Indicators
fig.add_trace(go.Candlestick(x=data.index, open=data['Open'], high=data['High'], low=data['Low'], close=data['Close'],
                             name="Price", increasing_line_color='limegreen', decreasing_line_color='firebrick'), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['MA20'], name='MA20', line=dict(color='orange')), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['MA50'], name='MA50', line=dict(color='blue')), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['BB_High'], name='BB High', line=dict(color='gray', dash='dot')), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['BB_Low'], name='BB Low', line=dict(color='gray', dash='dot')), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['Ichimoku_A'], name='Ichimoku A', line=dict(color='lightgreen', dash='dot')), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['Ichimoku_B'], name='Ichimoku B', line=dict(color='salmon', dash='dot')), row=1, col=1)

# Buy/Sell Markers
fig.add_trace(go.Scatter(x=data.index[data['Buy_Signal']], y=data['Close'][data['Buy_Signal']],
                         mode='markers', name='Buy', marker=dict(symbol='triangle-up', size=10, color='lime')), row=1, col=1)
fig.add_trace(go.Scatter(x=data.index[data['Sell_Signal']], y=data['Close'][data['Sell_Signal']],
                         mode='markers', name='Sell', marker=dict(symbol='triangle-down', size=10, color='red')), row=1, col=1)

# Fibonacci
for label, level in fibo_lines.items():
    fig.add_hline(y=level, line=dict(color='royalblue', dash='dot'), row=1, col=1)
    fig.add_annotation(text=f"Fibo {label}", xref="paper", x=1.0, y=level, yref="y1",
                       showarrow=False, font=dict(size=10, color="lightblue"), align="right")

# Row 2 - Volume
fig.add_trace(go.Bar(x=data.index, y=data['Volume'], name='Volume', marker_color='lightgray'), row=2, col=1)

# Row 3 - MACD
fig.add_trace(go.Scatter(x=data.index, y=data['MACD'], name='MACD', line=dict(color='cyan')), row=3, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['MACD_Signal'], name='MACD Signal', line=dict(color='magenta')), row=3, col=1)

# Row 4 - RSI + ADX
fig.add_trace(go.Scatter(x=data.index, y=data['RSI'], name='RSI', line=dict(color='violet')), row=4, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['ADX'], name='ADX', line=dict(color='yellow')), row=4, col=1)
fig.add_hline(y=70, line=dict(color='red', dash='dash'), row=4, col=1)
fig.add_hline(y=30, line=dict(color='green', dash='dash'), row=4, col=1)

# Row 5 - Stochastic + Support/Resistance
fig.add_trace(go.Scatter(x=data.index, y=data['Stoch_%K'], name='%K', line=dict(color='white')), row=5, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['Stoch_%D'], name='%D', line=dict(color='orange')), row=5, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['Support'], name='Support', line=dict(color='green', dash='dot')), row=5, col=1)
fig.add_trace(go.Scatter(x=data.index, y=data['Resistance'], name='Resistance', line=dict(color='red', dash='dot')), row=5, col=1)
fig.add_hline(y=80, line=dict(color='red', dash='dash'), row=5, col=1)
fig.add_hline(y=20, line=dict(color='green', dash='dash'), row=5, col=1)

# Layout
fig.update_layout(
    template='plotly_dark',
    title=dict(
        text=f"📈 NVDA Advanced Technical Analysis<br><sub>{start_date} to {end_date}</sub>",
        font=dict(size=24, color='white'),
        x=0.5,
        xanchor='center'
    ),
    height=1400,
    hovermode='x unified',
    xaxis_rangeslider_visible=False,
    legend=dict(
        orientation='h',
        yanchor='bottom',
        y=-0.35,
        xanchor='center',
        x=0.5,
        font=dict(size=12, color='white'),
        bgcolor='rgba(0,0,0,0)',
        bordercolor='gray',
        borderwidth=0
    ),
    margin=dict(l=60, r=30, t=80, b=100)
)

for i in range(1, 6):
    fig['layout'][f'yaxis{i}']['title'] = dict(
        text=fig['layout']['annotations'][i-1]['text'],
        font=dict(size=14, color='lightblue')
    )
fig['layout'].pop('annotations')

fig.show()

[*********************100%***********************]  1 of 1 completed


## **Moving Average Crossover Strategy: MA20 > MA50 on NVIDIA (NVDA)**

This section implements and evaluates a simple momentum-based **moving average crossover strategy** applied to NVIDIA (NVDA) stock. The strategy enters a long position when the 20-day moving average (MA20) crosses above the 50-day moving average (MA50), and exits (or goes short) when the opposite occurs.

---

### **Strategy Logic**
- **Buy Signal (`+1`)**: When `MA20 > MA50`
- **Sell Signal (`-1`)**: When `MA20 < MA50`
- **Positioning**: Based on the signal from the previous day (`shift(1)`), reflecting real-world delay in order execution.

---

### **Return Metrics**
- **Market Return**: Daily percentage change in adjusted close price
- **Strategy Return**: Return based on holding the position dictated by the crossover signal
- **Cumulative Performance**: Tracks the compound return over time for both the strategy and a passive buy-and-hold benchmark

---

### **Performance Summary**

| Metric             | Description                                                 |
|--------------------|-------------------------------------------------------------|
| **Total Return**   | Overall return generated by the strategy                    |
| **Benchmark Return** | Passive return from holding NVDA during the same period     |
| **Excess Return**  | Strategy return minus benchmark return                      |
| **Max Drawdown**   | Largest observed peak-to-trough decline                     |
| **Sharpe Ratio**   | Risk-adjusted return (assumes zero risk-free rate)          |
| **Win Rate**       | Proportion of days with positive strategy return            |

> The strategy's performance metrics are tabulated and visualized with an **equity curve plot**, facilitating direct comparison with the buy-and-hold approach.

---

This basic trend-following strategy forms a foundation for more complex rule-based or machine learning-enhanced trading systems.

---

In [94]:
# Configuration
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'

# Download Data
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=True)
data.dropna(inplace=True)

# Strategy Logic: MA20 > MA50
data['MA20'] = data['Close'].rolling(20).mean()
data['MA50'] = data['Close'].rolling(50).mean()
data['Signal'] = 0
data.loc[data['MA20'] > data['MA50'], 'Signal'] = 1
data.loc[data['MA20'] < data['MA50'], 'Signal'] = -1
data['Position'] = data['Signal'].shift(1)

# Return Calculations
data['Market_Return'] = data['Close'].pct_change()
data['Strategy_Return'] = data['Market_Return'] * data['Position']

data['Cumulative_Market'] = (1 + data['Market_Return']).cumprod()
data['Cumulative_Strategy'] = (1 + data['Strategy_Return']).cumprod()

# Performance Metrics
total_return = data['Cumulative_Strategy'].iloc[-1] - 1
benchmark_return = data['Cumulative_Market'].iloc[-1] - 1
excess_return = total_return - benchmark_return
max_drawdown = (data['Cumulative_Strategy'] / data['Cumulative_Strategy'].cummax() - 1).min()
sharpe_ratio = data['Strategy_Return'].mean() / data['Strategy_Return'].std() * np.sqrt(252)
win_rate = (data['Strategy_Return'] > 0).mean()

# Metrics Table (Enhanced)
metrics = pd.DataFrame({
    'Metric': ['Total Return', 'Benchmark Return', 'Excess Return', 'Max Drawdown', 'Sharpe Ratio', 'Win Rate'],
    'Strategy Value': [f"{total_return:.2%}", f"{benchmark_return:.2%}", f"{excess_return:.2%}",
                       f"{max_drawdown:.2%}", f"{sharpe_ratio:.2f}", f"{win_rate:.2%}"]
})

# Style the metrics table for a more professional look
styled_metrics = metrics.style.set_properties(**{'text-align': 'center'}).set_table_styles(
    [{'selector': 'th', 'props': [('text-align', 'center')]}]
).hide(axis="index")

display(HTML("<h3>Performance Metrics</h3>"))
display(styled_metrics)

# Equity Curve Plot (Interactive with Plotly)
if 'data' in globals() and 'Cumulative_Market' in data.columns and 'Cumulative_Strategy' in data.columns:
    fig = go.Figure()

    # Add Benchmark trace
    fig.add_trace(go.Scatter(
        x=data.index,
        y=data['Cumulative_Market'],
        mode='lines',
        name='Buy & Hold (Benchmark)',
        line=dict(color='gray', dash='dash'),
        hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Benchmark Return:</b> %{y:.2%}<extra></extra>'
    ))

    # Add Strategy trace
    fig.add_trace(go.Scatter(
        x=data.index,
        y=data['Cumulative_Strategy'],
        mode='lines',
        name='MA20 > MA50 Strategy',
        line=dict(color='green'),
        hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Strategy Return:</b> %{y:.2%}<extra></extra>'
    ))

    # Update layout for professional appearance
    fig.update_layout(
        title={
            'text': "📈 Strategy vs. Benchmark (Equity Curve)",
            'x': 0.5,
            'xanchor': 'center'
        },
        xaxis_title="Date",
        yaxis_title="Cumulative Return",
        template="plotly_white", # Clean white background
        hovermode="x unified",   # Show hover info for both traces on the same date
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=1.02,
            xanchor="right",
            x=1
        ),
        margin=dict(l=40, r=40, t=40, b=40) # Adjust margins
    )

    # Display the interactive plot
    display(HTML("<h3>Equity Curve</h3>"))
    fig.show()
else:
    print("⚠️ Cannot plot equity curve: 'data' DataFrame or required columns not found.")


[*********************100%***********************]  1 of 1 completed


## **Drawdown Analysis: Strategy vs. Buy & Hold Benchmark**

This section presents an interactive drawdown analysis to evaluate the downside risk of the moving average crossover strategy in comparison with a passive benchmark (Buy & Hold) for NVIDIA (NVDA).

---

### **What is Drawdown?**
Drawdown measures the **percentage decline from a historical peak in cumulative returns**. It is a key metric to assess:
- **Capital preservation**
- **Strategy resilience during downturns**
- **Risk-adjusted performance**

---

### **Methodology**
For each time point:
- **Strategy Drawdown** = $( \frac{Cumulative\_Strategy}{Peak\_Strategy} - 1)$
- **Benchmark Drawdown** = $( \frac{Cumulative\_Market}{Peak\_Market} - 1)$

Both are visualized using shaded `Plotly` line charts:
- 🟥 **Strategy Drawdown** (filled dark red)
- ⬜ **Benchmark Drawdown** (dashed gray)

---

### **Interpretation Guidelines**
- A **deeper drawdown** indicates higher historical losses.
- **Faster recoveries** and **shallower drawdowns** suggest greater strategy robustness.
- Comparing drawdowns side-by-side helps identify whether active management provided superior downside protection.

---

> **Important:** While total return is important, **maximum drawdown is critical** for understanding the strategy's real-world sustainability under stress conditions.


In [95]:
# Drawdown Analysis Plot (Interactive)

# Ensure required data is available
if 'data' in globals() and 'Cumulative_Strategy' in data.columns and 'Cumulative_Market' in data.columns:

    try:
        # Calculate Peak for Strategy
        data['Peak_Strategy'] = data['Cumulative_Strategy'].cummax()
        # Calculate Drawdown for Strategy
        data['Drawdown_Strategy'] = data['Cumulative_Strategy'] / data['Peak_Strategy'] - 1

        # Calculate Peak for Benchmark
        data['Peak_Market'] = data['Cumulative_Market'].cummax()
        # Calculate Drawdown for Benchmark
        data['Drawdown_Market'] = data['Cumulative_Market'] / data['Peak_Market'] - 1

        # Create interactive Plotly figure
        fig_drawdown = go.Figure()

        # Add Strategy Drawdown trace
        fig_drawdown.add_trace(go.Scatter(
            x=data.index,
            y=data['Drawdown_Strategy'],
            mode='lines',
            name='Strategy Drawdown',
            line=dict(color='darkred'),
            fill='tozeroy',
            fillcolor='rgba(139, 0, 0, 0.3)',
            hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Strategy Drawdown:</b> %{y:.2%}<extra></extra>'
        ))

        # Add Benchmark Drawdown trace
        fig_drawdown.add_trace(go.Scatter(
            x=data.index,
            y=data['Drawdown_Market'],
            mode='lines',
            name='Benchmark Drawdown',
            line=dict(color='darkgray', dash='dash'),
            fill='tozeroy',
            fillcolor='rgba(169, 169, 169, 0.3)',
            hovertemplate='<b>Date:</b> %{x|%Y-%m-%d}<br><b>Benchmark Drawdown:</b> %{y:.2%}<extra></extra>'
        ))

        # Update layout for professional appearance
        fig_drawdown.update_layout(
            title={
                'text': "📉 Strategy vs. Benchmark (Drawdown Analysis)",
                'x': 0.5,
                'xanchor': 'center'
            },
            xaxis_title="Date",
            yaxis_title="Drawdown (%)",
            template="plotly_white",
            hovermode="x unified",
            legend=dict(
                orientation="h",
                yanchor="bottom",
                y=1.02,
                xanchor="right",
                x=1
            ),
            margin=dict(l=40, r=40, t=40, b=40),
            yaxis_tickformat=".0%",
        )

        # Display the interactive plot
        display(HTML("<h3>Drawdown Analysis</h3>"))
        fig_drawdown.show()

    except Exception as e:
        print(f"❌ Error during drawdown calculation or plotting: {e}")

else:
    print("⚠️ Cannot plot drawdown analysis: 'data' DataFrame or required cumulative return columns not found.")

## **Grid Search Optimization for Moving Average Crossover Strategy**

This section performs a **systematic grid search** over a range of fast and slow moving average (MA) window combinations to evaluate and compare the performance of various crossover strategies for NVDA stock.

---

### **Configuration**
**Strategy Logic:** Long when `MA_fast > MA_slow`, short otherwise (using shifted position for realistic execution)

---

### **Grid Search Parameters**
| Parameter    | Range              | Explanation                            |
|--------------|--------------------|----------------------------------------|
| `MA_Fast`    | 10, 15, 20, 25, 30 | Short-term moving average windows      |
| `MA_Slow`    | 40, 50, 60, 70, 80 | Long-term moving average windows       |

Combinations where `MA_Fast >= MA_Slow` are **excluded**, as they violate the strategy’s trend-following logic.

---

### **Performance Metrics Computed**
For each parameter pair:
- **Total Return** = Final cumulative return of the strategy
- **Sharpe Ratio** = Risk-adjusted return (annualized using √252)

---

### **Visualization: Sharpe Ratio Heatmap**

The heatmap displays Sharpe Ratios across all valid `MA_Fast`–`MA_Slow` pairs:
- **X-axis:** Slow MA window
- **Y-axis:** Fast MA window
- **Color scale:** Intensity of risk-adjusted return

This visual insight allows quick identification of optimal combinations based on risk-adjusted performance rather than raw return alone.

---

> **Conclusion**: Grid search optimization is a powerful tool for identifying robust parameter sets in rule-based trading strategies, avoiding overfitting and exposing trade-offs between return and risk.

---

In [96]:
# Configuration
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=True).dropna()

# Grid Search Parameters
fast_windows = range(10, 31, 5)   # e.g. 10, 15, 20, 25, 30
slow_windows = range(40, 81, 10)  # e.g. 40, 50, 60, 70, 80

results = []

for fast in fast_windows:
    for slow in slow_windows:
        if fast >= slow:
            continue

        temp = data.copy()
        temp['MA_fast'] = temp['Close'].rolling(fast).mean()
        temp['MA_slow'] = temp['Close'].rolling(slow).mean()
        temp['Signal'] = np.where(temp['MA_fast'] > temp['MA_slow'], 1, -1)
        temp['Position'] = temp['Signal'].shift(1)

        temp['Return'] = temp['Close'].pct_change()
        temp['Strategy_Return'] = temp['Position'] * temp['Return']
        temp['Cumulative'] = (1 + temp['Strategy_Return']).cumprod()

        sharpe = temp['Strategy_Return'].mean() / temp['Strategy_Return'].std() * np.sqrt(252)
        total_return = temp['Cumulative'].iloc[-1] - 1

        results.append({
            'MA_Fast': fast, 'MA_Slow': slow,
            'Sharpe_Ratio': sharpe, 'Total_Return': total_return
        })

# DataFrame
df_results = pd.DataFrame(results)

# Heatmap: Sharpe Ratio
pivot = df_results.pivot(index='MA_Fast', columns='MA_Slow', values='Sharpe_Ratio')
fig = px.imshow(pivot, text_auto=".2f", aspect="auto",
                labels=dict(x="MA Slow", y="MA Fast", color="Sharpe Ratio"),
                title="📈 Sharpe Ratio Grid Search – MA Fast vs MA Slow")
fig.update_layout(template='plotly_dark', height=600)
fig.show()


[*********************100%***********************]  1 of 1 completed


## **Trade Log Analysis for MA20 > MA50 Strategy (NVDA)**

This section identifies and records **individual trades** generated by the moving average crossover strategy applied to NVIDIA (NVDA), where a position is taken when the 20-day moving average exceeds the 50-day moving average.

---

### **Strategy Signal Logic**
- **Buy Signal:** Triggered when `MA20` crosses **above** `MA50` (i.e., momentum shift upward)
- **Sell Signal:** Triggered when `MA20` crosses **below** `MA50` (i.e., trend reversal downward)
- **Positioning:** Strategy enters and exits based on these crossover events (with 1-day lag for execution realism)

---

### **Trade Detection and Matching**
- The algorithm detects **trade events** using the change in `Position` values.
- A **Buy–Sell pair** is matched to create one complete trade.
- Each trade includes:
  - Entry and exit dates
  - Entry and exit prices
  - Holding duration (in calendar days)
  - Profit/Loss (absolute and percentage terms)

---

### **Trade Log Table Output**

| Column         | Description                                          |
|----------------|------------------------------------------------------|
| `Entry_Date`   | Date the long position was initiated (buy signal)    |
| `Entry_Price`  | Price at which the position was opened               |
| `Exit_Date`    | Date the position was closed (sell signal)           |
| `Exit_Price`   | Price at which the position was closed               |
| `Holding_Days` | Duration between entry and exit                      |
| `PnL_Abs`      | Absolute profit or loss                              |
| `PnL_%`        | Return on trade in percentage terms                  |

> This structured trade log enables micro-level evaluation of strategy performance across multiple trades, supporting deeper diagnostics such as **average return**, **win rate**, and **holding period analysis**.

---

In [97]:
# Configuration
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=True).dropna()

# Strategy Definition: Buy if MA20 > MA50
data['MA20'] = data['Close'].rolling(20).mean()
data['MA50'] = data['Close'].rolling(50).mean()
data['Signal'] = np.where(data['MA20'] > data['MA50'], 1, -1)
data['Position'] = data['Signal'].shift(1)

# Detect Trade Events
data['Trade_Event'] = data['Position'].diff()
trade_points = data[(data['Trade_Event'] == 2) | (data['Trade_Event'] == -2)].copy()
trade_points['Action'] = np.where(trade_points['Trade_Event'] == 2, 'Buy', 'Sell')
trade_points['Price'] = trade_points['Close']
trade_points['Date'] = trade_points.index

# Match Buy and Sell Trades
trades = []
entry = None

for index, row in trade_points.iterrows():
    if row['Action'].item() == 'Buy':
        entry = row
    elif row['Action'].item() == 'Sell' and entry is not None:
        exit_ = row
        trades.append({
            'Entry_Date': entry['Date'].item(),
            'Entry_Price': round(entry['Price'].item(), 2),
            'Exit_Date': exit_['Date'].item(),
            'Exit_Price': round(exit_['Price'].item(), 2),
            'Holding_Days': (exit_['Date'].item() - entry['Date'].item()).days,
            'PnL_Abs': round(exit_['Price'].item() - entry['Price'].item(), 2),
            'PnL_%': round((exit_['Price'].item() / entry['Price'].item() - 1) * 100, 2)
        })
        entry = None

# Trade Log Table
trade_log = pd.DataFrame(trades)
trade_log = trade_log[['Entry_Date', 'Entry_Price', 'Exit_Date', 'Exit_Price', 'Holding_Days', 'PnL_Abs', 'PnL_%']]
trade_log.sort_values(by='Entry_Date', inplace=True)
trade_log.reset_index(drop=True, inplace=True)
display(trade_log)

[*********************100%***********************]  1 of 1 completed


Entry_Date  Entry_Price  Exit_Date  Exit_Price  Holding_Days  PnL_Abs  PnL_%
0 2024-03-14        87.92 2024-05-01       83.01            48    -4.90  -5.58
1 2024-05-21        95.35 2024-08-05      100.43            76     5.07   5.32
2 2024-09-09       106.44 2024-09-20      115.98            11     9.54   8.96
3 2024-10-03       122.83 2024-12-18      128.90            76     6.07   4.94

## **Cumulative PnL Analysis for MA20 > MA50 Strategy (NVDA)**

This section calculates and visualizes the **cumulative profit and loss (PnL)** of each completed trade generated by the moving average crossover strategy applied to NVIDIA (NVDA). The focus is on evaluating how the strategy performs over time in terms of accumulated profit.

---

### **Strategy Workflow Recap**
- **Buy Entry:** Triggered when `MA20` crosses **above** `MA50`
- **Sell Exit:** Triggered when `MA20` crosses **below** `MA50`
- **PnL Calculation:** Difference between exit and entry prices
- **Cumulative PnL:** Sum of all realized trade profits/losses over time

---

### **Visualization: Cumulative PnL Curve**

- **X-axis:** Trade exit dates
- **Y-axis:** Cumulative realized profit ($)
- **Trace:** A line + marker chart showing how the strategy’s profit grows (or declines) as trades accumulate

This plot offers a **clear diagnostic tool** for understanding:
- Periods of strong profitability
- Consecutive losing trades (visible as drawdowns)
- Strategy consistency over time

---

### **Interpretation**

| Indicator                  | Insight                                                      |
|---------------------------|--------------------------------------------------------------|
| Upward-sloping PnL curve  | Strategy is generating positive returns over time           |
| Flat sections             | Periods with no new trades or net-zero PnL                  |
| Sharp declines            | Consecutive losses or a significant negative trade           |

> 📊 The cumulative PnL graph is a practical complement to backtest metrics like Sharpe Ratio or Drawdown, offering **trade-level clarity** on profitability evolution.

---

In [98]:
# NVDA and strategy implementation
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=True).dropna()

# MA20 > MA50 strategy
data['MA20'] = data['Close'].rolling(20).mean()
data['MA50'] = data['Close'].rolling(50).mean()
data['Signal'] = np.where(data['MA20'] > data['MA50'], 1, -1)
data['Position'] = data['Signal'].shift(1)
data['Trade_Event'] = data['Position'].diff()

# Identify buy and sell points
trades_raw = data[(data['Trade_Event'] == 2) | (data['Trade_Event'] == -2)].copy()
trades_raw['Action'] = np.where(trades_raw['Trade_Event'] == 2, 'Buy', 'Sell')
trades_raw['Price'] = trades_raw['Close']
trades_raw['Date'] = trades_raw.index

# Match transactions and calculate PnL
trades = []
entry = None
for _, row in trades_raw.iterrows():
    if row['Action'].item() == 'Buy':
        entry = row

    elif row['Action'].item() == 'Sell' and entry is not None:
        pnl = row['Price'].item() - entry['Price'].item()
        trades.append({
            'Entry_Date': entry['Date'].item(),
            'Entry_Price': entry['Price'].item(),
            'Exit_Date': row['Date'].item(),
            'Exit_Price': row['Price'].item(),
            'PnL': pnl,
            'PnL_%': (row['Price'].item() / entry['Price'].item() - 1) * 100
        })
        entry = None

trade_log = pd.DataFrame(trades)
trade_log['Cumulative_PnL'] = trade_log['PnL'].cumsum()

# Graph: Cumulative PnL Curve
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=trade_log['Exit_Date'],
    y=trade_log['Cumulative_PnL'],
    mode='lines+markers',
    name='Cumulative PnL',
    line=dict(color='limegreen', width=3),
    marker=dict(size=6),
    hovertemplate="<b>%{x|%Y-%m-%d}</b><br>Cumulative PnL: %{y:.2f}<extra></extra>"
))

fig.update_layout(
    title="📈 Cumulative Profit Curve – MA20 > MA50 Strategy",
    xaxis_title="Exit Date",
    yaxis_title="Cumulative PnL ($)",
    template="plotly_dark",
    hovermode="x unified",
    height=500,
    margin=dict(l=60, r=40, t=60, b=40)
)

fig.show()

[*********************100%***********************]  1 of 1 completed


## **Drawdown Curve Analysis for MA20 > MA50 Strategy (NVDA)**

This section visualizes the **drawdown behavior** of the moving average crossover strategy applied to NVIDIA (NVDA), providing insight into the strategy’s downside risk profile over the selected trading period.

---

### **What is Drawdown?**
- **Drawdown** measures the decline of the strategy's cumulative return from its historical peak.
- It highlights the **worst-case capital erosion** an investor might experience if they entered at a previous high.

---

### **Calculation Details**
- **Strategy Return:** Calculated daily using the position from the previous day and market return
- **Cumulative Return:** Product of (1 + strategy returns)
- **Peak:** Running maximum of cumulative return
- **Drawdown:**  
  \[
  \text{Drawdown} = \frac{Cumulative\_Strategy}{Peak} - 1
  \]
- **Max Drawdown:** The deepest observed drawdown over the backtesting period

---

### **Visualization: Drawdown Chart**
- **Y-axis:** Drawdown expressed as a percentage
- **X-axis:** Date
- **Trace:** Crimson line representing daily drawdown
- **Sub-title:** Displays the **Maximum Drawdown** as a key risk metric

This chart helps investors understand how severely and how long a strategy can deviate from its best performance point.

---

### **Interpretation**

| Metric         | Meaning                                            |
|----------------|----------------------------------------------------|
| **Sharp Dips** | Strategy experienced significant loss periods      |
| **Flat Zones** | Stable performance near previous highs             |
| **Max DD**     | Reflects historical worst-case loss scenario       |

> Even strategies with positive average returns can suffer large drawdowns. This makes **drawdown analysis essential** for evaluating **strategy robustness** and **risk-adjusted performance**.

---

In [99]:
# Configuration
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=True).dropna()

data['MA20'] = data['Close'].rolling(20).mean()
data['MA50'] = data['Close'].rolling(50).mean()
data['Signal'] = np.where(data['MA20'] > data['MA50'], 1, -1)
data['Position'] = data['Signal'].shift(1)

# Strategy Return and Drawdown
data['Return'] = data['Close'].pct_change()
data['Strategy_Return'] = data['Return'] * data['Position']
data['Cumulative_Strategy'] = (1 + data['Strategy_Return']).cumprod()

data['Peak'] = data['Cumulative_Strategy'].cummax()
data['Drawdown'] = (data['Cumulative_Strategy'] / data['Peak']) - 1

# Maximum Drawdown Value
max_dd = data['Drawdown'].min()

# Drawdown Graph
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=data.index,
    y=data['Drawdown'],
    mode='lines',
    name='Drawdown',
    line=dict(color='crimson', width=2),
    hovertemplate="<b>%{x|%Y-%m-%d}</b><br>Drawdown: %{y:.2%}<extra></extra>"
))

fig.update_layout(
    title=f"📉 Drawdown Analysis – MA20 > MA50 Strategy<br><sub>Max Drawdown: {max_dd:.2%}</sub>",
    xaxis_title="Date",
    yaxis_title="Drawdown (%)",
    template="plotly_dark",
    height=500,
    hovermode="x unified",
    margin=dict(l=60, r=40, t=60, b=40)
)

fig.show()


[*********************100%***********************]  1 of 1 completed


## **Monte Carlo Simulation of Cumulative PnL – MA20 > MA50 Strategy (NVDA)**

This section employs a **Monte Carlo Simulation** to assess the forward-looking uncertainty and risk of the MA20 > MA50 trading strategy applied to NVIDIA (NVDA). It generates a distribution of possible future outcomes by resampling historical daily returns.

---

### **Methodology**

#### 1. **Data Preparation**
- Strategy returns are computed based on historical crossover signals.
- Only non-NaN daily strategy returns are retained for sampling.

#### 2. **Simulation Parameters**
| Parameter         | Value               | Description                                     |
|-------------------|---------------------|-------------------------------------------------|
| `n_simulations`   | 500                 | Number of simulated paths                       |
| `n_days`          | 252                 | Number of business days (≈ 1 trading year)      |
| `Sampling Method` | Bootstrap with replacement | Historical return resampling                    |

Each simulated path represents a plausible cumulative return trajectory under similar statistical conditions observed in the past.

---

### **Visualization: Monte Carlo Return Paths**

- **Shaded Area:** 5th–95th percentile range (confidence interval)
- **Line (Green):** Mean cumulative return path
- **X-axis:** Simulated forward dates
- **Y-axis:** Cumulative return relative to starting point (normalized to 1.0)

This chart helps estimate the **distribution of returns**, possible **risk exposure**, and **best/worst-case scenarios** for the strategy.

---

### **Interpretation**

| Component                      | Insight                                                                 |
|--------------------------------|-------------------------------------------------------------------------|
| **Wider bands**                | Higher uncertainty and potential volatility                            |
| **Mean Path Slopes Upward**    | Strategy is positively biased on average                               |
| **Lower Band Approaches 0**    | Indicates chance of underperformance or capital erosion                |

> While past returns are not predictive, **Monte Carlo analysis provides a probabilistic framework** for anticipating future strategy outcomes under similar market conditions.

---

In [100]:
# Step 1: Get Data and Apply Strategy
ticker = 'NVDA'
start_date = '2024-01-01'
end_date = '2025-06-06'
data = yf.download(ticker, start=start_date, end=end_date, interval='1d', auto_adjust=True).dropna()

data['MA20'] = data['Close'].rolling(20).mean()
data['MA50'] = data['Close'].rolling(50).mean()
data['Signal'] = np.where(data['MA20'] > data['MA50'], 1, -1)
data['Position'] = data['Signal'].shift(1)

data['Daily_Return'] = data['Close'].pct_change()
data['Strategy_Return'] = data['Daily_Return'] * data['Position']
returns = data['Strategy_Return'].dropna()

# Step 2: Monte Carlo Simulation
np.random.seed(42)
n_simulations = 500
n_days = 252  # 1 yıl

simulations = []
for _ in range(n_simulations):
    sampled = np.random.choice(returns, size=n_days, replace=True)
    cumulative = (1 + sampled).cumprod()
    simulations.append(cumulative)

sim_df = pd.DataFrame(simulations).T
sim_df.index = pd.date_range(start='2025-06-07', periods=n_days, freq='B')

# Step 3: Summary Statistics
sim_df['Mean'] = sim_df.mean(axis=1)
sim_df['P05'] = sim_df.quantile(0.05, axis=1)
sim_df['P95'] = sim_df.quantile(0.95, axis=1)

# Step 4: Plot
fig = go.Figure()

fig.add_trace(go.Scatter(x=sim_df.index, y=sim_df['P95'], mode='lines',
                         line=dict(width=0), showlegend=False))
fig.add_trace(go.Scatter(x=sim_df.index, y=sim_df['P05'], mode='lines',
                         fill='tonexty', fillcolor='rgba(255,0,0,0.2)', line=dict(width=0),
                         name='5–95% Confidence Interval'))
fig.add_trace(go.Scatter(x=sim_df.index, y=sim_df['Mean'], mode='lines',
                         name='Mean Path', line=dict(color='lime', width=2)))

fig.update_layout(
    title="🎲 Monte Carlo Simulation of PnL – MA20 > MA50 Strategy",
    xaxis_title="Simulated Days",
    yaxis_title="Cumulative Return",
    template="plotly_dark",
    hovermode="x unified",
    height=500,
    margin=dict(l=60, r=40, t=60, b=40)
)

fig.show()


[*********************100%***********************]  1 of 1 completed


# **References**

- Kresta, A. (2024). *Applied Quantitative Finance in Python: Selected Theories and Examples*. Retrieved from [ResearchGate](https://www.researchgate.net/publication/386032446_Applied_Quantitative_Finance_in_Python_Selected_theories_and_examples)
